In [89]:
import argparse
import numpy as np
import random
import argparse
import os
import time
import math
import sys
import json
import csv
import pandas as pd
from itertools import chain
import natsort
import collections

import torch
from torch.autograd import Variable

from sklearn.metrics.pairwise import euclidean_distances, cosine_distances

from models import load_models_decode, generate
from utils import to_gpu, Corpus, batchify, train_ngram_lm, get_ppl

# Raw data

In [2]:
load_path='output/out1102'
# load_path='output/out_twitter1103'
# load_path='output/out1106_komoran'
# load_path='output/outparsing1204'
# load_path='output/output1207_newdata2'
# load_path='output/output1207_newdata_komoran'

In [3]:
idx2word, autoencoder, gan_gen, gan_disc, word2idx= load_models_decode(load_path)

Loading models fromoutput/out1102


In [8]:
# vocab2=idx2word
# vocab2
# word2idx

{0: '<pad>',
 1: '<sos>',
 2: '<eos>',
 3: '<oov>',
 4: '가',
 5: '가.',
 6: '가가',
 7: '가거나',
 8: '가게',
 9: '가게가도',
 10: '가게나',
 11: '가게되면',
 12: '가게되었으며',
 13: '가게마다',
 14: '가게에',
 15: '가게에서',
 16: '가게에서나',
 17: '가게주인이주어서.',
 18: '가격',
 19: '가격.',
 20: '가격과',
 21: '가격까지',
 22: '가격대',
 23: '가격대가',
 24: '가격대가있지만',
 25: '가격대도',
 26: '가격대로',
 27: '가격대비',
 28: '가격대에',
 29: '가격대와',
 30: '가격대중성.',
 31: '가격도',
 32: '가격도싸고',
 33: '가격면에서',
 34: '가격보다도',
 35: '가격부담없이',
 36: '가격에',
 37: '가격에다',
 38: '가격에서',
 39: '가격은',
 40: '가격을',
 41: '가격이',
 42: '가격이랑',
 43: '가격이싸고',
 44: '가격저렴.',
 45: '가격저렴하고',
 46: '가격적으로나',
 47: '가격적으로도',
 48: '가격적인',
 49: '가격차이',
 50: '가격치곤',
 51: '가고',
 52: '가공공법',
 53: '가기',
 54: '가까운',
 55: '가까운데서',
 56: '가까운맛.',
 57: '가까움',
 58: '가까움.',
 59: '가까이서',
 60: '가까이에서',
 61: '가깝게',
 62: '가깝다고',
 63: '가끔',
 64: '가끔가다',
 65: '가끔식',
 66: '가끔씩',
 67: '가나',
 68: '가는',
 69: '가는거같다.',
 70: '가는구간에도',
 71: '가는데',
 72: '가는듯한',
 73: '가능.',
 74: '가능하고',
 75: '가능하다',
 76: '가능하다.',
 77: '가능하며

In [4]:
path_raw = 'codedata/1207basic/DBSCAN_result_Topic_refined.csv'
maxlen=100

In [148]:
# path_raw = 'codedata/1207basic/DBSCAN_result_Topic_refined_Parsed.csv'
# maxlen=100

In [7]:
data = pd.read_csv(path_raw, names = None,encoding='cp949')
clusternum=data['clusterno']
docno = data['docNo']
doc = data['raw_doc']

In [6]:
################Komoran 단위
from konlpy.tag import Komoran

pos_tagger = Komoran()

def tokenize_komoran(doc):
    # norm, stem은 optional
    return [x for x, t in pos_tagger.pos(doc)]

token = []
for row in doc :
    token.append(' '.join(k for k in tokenize_komoran(row)))

data['raw_doc']= pd.DataFrame(token)[0]
tokendoc = data['raw_doc']

data

KeyboardInterrupt: 

In [8]:
# {clusterno : [doc]}
groupby_cluster = doc.groupby([clusternum])
cluster_doc_rawdata=groupby_cluster.apply(lambda x: x.tolist()).to_dict()
# dbscan 노이즈 결과 버리기
del cluster_doc_rawdata['-1']

    
# {clusterno : [docno]}
docno_groupby_cluster = docno.groupby([clusternum])
docno_cluster=docno_groupby_cluster.apply(lambda x: x.tolist()).to_dict()
# dbscan 노이즈 결과 버리기
del docno_cluster['-1']

In [223]:
docno_cluster

{'0': [8828,
  2951,
  8632,
  8448,
  10013,
  5086,
  9394,
  8762,
  5763,
  7968,
  908,
  297,
  1554,
  5961,
  3432,
  7292,
  2549,
  7396,
  1014,
  5772,
  8129,
  4148,
  7057,
  4203,
  3651,
  6459,
  6809,
  2446,
  9155,
  4528,
  6088,
  6316,
  4564,
  3333,
  10344,
  8856,
  9480,
  6619,
  4042,
  8584,
  9567,
  3351,
  6368,
  8203,
  9274,
  2526,
  2724,
  4745,
  2465,
  9027,
  3977,
  8379,
  1954,
  8663,
  6220,
  6203,
  9195,
  1898,
  3608,
  4328,
  10076,
  9526,
  794,
  2159,
  3360,
  5012,
  4060,
  64,
  8392,
  8105,
  809,
  4673,
  5549,
  4684,
  9748,
  2477,
  8941,
  7083,
  7676,
  3755,
  3637,
  5386,
  4460,
  4761,
  7867,
  8844,
  10188,
  8596,
  3476,
  1777,
  2551,
  4044,
  2779,
  2867,
  9012,
  4524,
  753,
  1205,
  7080,
  8771,
  4724,
  3469,
  5674,
  3958,
  3255,
  10216,
  9928,
  9729,
  9602,
  2913,
  1808,
  3972,
  3908,
  8340,
  1701,
  775,
  4652,
  3,
  3038,
  8327,
  1959,
  6899,
  5925,
  1081,
  7659,
 

In [9]:
#마지막 결과표에 쓰기 위해 모든 docno를 순서대로 하나의 리스트로
li_docno=list(docno_cluster.values())
li_docno = list(chain.from_iterable(li_docno))
len(li_docno)

8379

In [238]:
##########Komoran
groupby_cluster_token = tokendoc.groupby([clusternum])
cluster_doc=groupby_cluster_token.apply(lambda x: x.tolist()).to_dict()
if '-1' in cluster_doc.keys():
    del cluster_doc['-1']

In [181]:
cluster_doc_rawdata

{0: ['큰 효과를 보지는 못함.',
  '효과',
  '효과가 바로 와닿지가 않는다.  \r\n\r\n',
  '효과가 그다지..',
  '효과가 좋다',
  '신속셩 효과',
  '효과없음',
  '효과가 있다',
  '효과가 좋아서',
  '효과가좋다',
  '효과가있다',
  '효과가 신속하게 나서',
  '효과가 있었다',
  '즉시효과',
  '효과를 봤다.',
  '효과가 좋았었다',
  '효과가 좋다',
  '효과좋음',
  '신속한 효과',
  '효과가 신속함',
  '효과가 있으니까',
  '효과가 좋기떄문에',
  '효과가좋다',
  '효과가 있다',
  '큰 효과가 없었음',
  '효과가 좋았음',
  '효과가 좋았다.',
  '효과가 좋다',
  '효과가 그리 좋지 않아서',
  '효과가 딱히 없음',
  '효과적임',
  '효과있어서',
  '효과가 신속함',
  '신속하고 효과적임',
  '효과가 좋아서',
  '효과가 좋아서',
  '효과가 좋아서',
  '효과 별로',
  '효과가 좋아서',
  '효과가 있어서',
  '효과가 좋다',
  '효과가 있음',
  '큰효과는 아직 잘 모르겠ㄸ다',
  '효과가 있어서',
  '크게 효과를 보지 못해서',
  '효과있다',
  '효과가 좋다',
  '신속한 효과',
  '효과가 신속',
  '효과가 좋다',
  '효과가 있어서',
  '효과가 좋음',
  '효과좋음',
  '효과가 별로',
  '효과가 좋음',
  '효과가 별로',
  '효과가 좋음'],
 1: ['효과가 빠르다',
  '사용 편리성과 빠른 효과,효능 때문에',
  '효과가 빠름',
  '편리성 지속성',
  '효과가 빠른 편이다',
  '효과가 빠르다',
  '효과가 빠르고 진정이 잘 되서',
  '효과가 지속되지않아서',
  '사용할 때 효과가 빠르게 나타나서',
  '효과가 빠르다',
  '편하고 효과도 빠름',
  '효과가 바로 나타난다',
  '효과가 빠르다',
  '바로 효과가 나타나서',
  '효과가 빠름

In [10]:
vocab = word2idx
ntokens = len(vocab)

def doc_to_line(cluster_doc, vocab):

    dropped = 0
    linecount = 0
    lines = []
    for line in cluster_doc:
        linecount += 1        
#         if self.lowercase:
#             words = line[:-1].lower().strip().split(" ")
#         else:
#             words = line[:-1].strip().split(" ")
        words = line[:-1].strip().split(" ")
        
        if len(words) > maxlen:
            dropped += 1
            continue
        words = ['<sos>'] + words
        words += ['<eos>']

        # vectorize

        unk_idx = vocab['<oov>']
        indices = [vocab[w] if w in vocab else unk_idx for w in words]

#         print(indices)
        lines.append(indices)
        
    return lines, vocab

In [11]:
def make_code(lines):
    eval_batch_size = 1
    test_data = batchify(lines, eval_batch_size, shuffle=False)
     
    code = []
    for i, batch in enumerate(test_data):
            source, target, lengths = batch
    #         source = to_gpu(True, Variable(source, volatile=True))
    #         target = to_gpu(True, Variable(target, volatile=True))
    #         mask = target.gt(0)
    #         masked_target = target.masked_select(mask)
    #         # examples x ntokens
    #         output_mask = mask.unsqueeze(1).expand(mask.size(0), ntokens)

            # output: batch x seq_len x ntokens
            output = autoencoder.encode(Variable(source), lengths, noise=False)
#             print(output)
            code.append(output)
    return code

In [12]:
title_raw_eucli={}
title_raw_cosine={}

num_title_raw_eucli={}
num_title_raw_cosine={}

# title_eucli={}
# title_cosine={}

for c in cluster_doc_rawdata.keys() : 
    
########Komoran
# for c in cluster_doc.keys() :     


    lines, vocab = doc_to_line(cluster_doc_rawdata[c], vocab)
    
########Komoran    
#     lines, vocab = doc_to_line(cluster_doc[c], vocab)

    code = make_code(lines)

    code_cat=torch.cat(code,0)

    #code_feature extract(절대값 0.1미만 0으로)
#     code_cat_np = code_cat.data.numpy().squeeze()
#     temp = np.copy(code_cat_np)
#     temp[np.where(np.abs(temp)<feature_range)]=0
#     code_feature=torch.FloatTensor(temp).view(-1,300)

    #code 평균
    code_mean=torch.mean(code_cat,0).view(1,-1)

    #code 평균과 길이가 최소인 vector 구하기
    input1 = code_cat.data.numpy()
    mean_np = code_mean.data.numpy()
    eucli = euclidean_distances(input1, mean_np).squeeze()
    cosine = cosine_distances(input1, mean_np).squeeze()
    
    #{clusterno : title}
    title_raw_eucli[c]=cluster_doc_rawdata[c][np.argmin(eucli)]
    title_raw_cosine[c]=cluster_doc_rawdata[c][np.argmin(cosine)]
    
    #{clusterno : title num}
    num_title_raw_eucli[c]=docno_cluster[c][np.argmin(eucli)]
    num_title_raw_cosine[c]=docno_cluster[c][np.argmin(cosine)]
        
    ############Komoran인 경우
#     title_eucli[c]=cluster_doc_rawdata[c][np.argmin(eucli)]
#     title_cosine[c]=cluster_doc_rawdata[c][np.argmin(cosine)]

In [181]:
title_raw_eucli

{'0': '시원하다',
 '1': '맛이 깔끔해서',
 '10': '고급스럼',
 '100': '1. 수입 맥주 중에서는 꽤 저렴한 편  2. 특별한 향이 없다. (과일향 같은 것이 나는 맥주를 개인적으로 싫어함)  3. 디자인이 마음에 든다. (빨간색)',
 '101': '톡쏘는 느낌이 좋아서',
 '102': '맛이 달콤하다',
 '103': '깔끔하고 한 눈에 들어온다. 익숙하다',
 '104': '세련됨',
 '105': '진짜 보리로 만든다는 느낌의 색갈이 상표 이름에 들어가있어서',
 '106': '다이어트',
 '107': '여러종류의 맥주를 마셔봤는데 가장 청량함이좋은것 같고  마시고난뒤 깔끔함을 느낄수있어서',
 '108': '텔레비젼 광고를 보고 . 시원하고 상쾌할 것 같은 맛 때문',
 '109': 'it has to be a heineken  맛이나 광고나...하이네켄 신봉자 입니다+_+',
 '11': '맛이 시원하고 깔끔합니다',
 '110': '미국꺼라서그런지',
 '111': '보편적이라',
 '112': '다른 맥주와 차별화 된 맛',
 '113': '간단해서',
 '114': '습관적으로',
 '115': '병으로 앙증맞게 있어서 먹기도 좋고 먹을때 기분이 좋아서.. \r\n\r\n목넘김이 부드러워서',
 '116': '하정우',
 '117': '초기 CF의 독특한 카피..  눈으로 마시는 맥주',
 '118': '기본',
 '119': '시원한느낌이 들고..  제가 즐겨먹는맥주라서~',
 '12': '자주 마셔서',
 '120': '여자이다보니 다른 맥주에 비해 칼로리가 낮고 부드러워서 삼켜서 목구멍에 들어가는 느낌이 따갑지 않아 좋아요',
 '121': '과일향이 입맛에 맞는다. 전용잔에 따라먹는 재미',
 '122': '내입에맞아서',
 '123': '이미지, 오랬동안 마셔와서 습관적으로',
 '124': '국산맥주들은 맛이 다 비슷한데 오비골든라거는 약간 맛이 다르고 맛있습니다',
 '125': '오래되서',
 '126

In [180]:
num_title_raw_eucli

{'0': 8828,
 '1': 9793,
 '10': 1638,
 '100': 5195,
 '101': 2692,
 '102': 8611,
 '103': 4222,
 '104': 8444,
 '105': 9253,
 '106': 9485,
 '107': 4296,
 '108': 5594,
 '109': 1529,
 '11': 4321,
 '110': 4045,
 '111': 5201,
 '112': 3193,
 '113': 7203,
 '114': 7618,
 '115': 2710,
 '116': 4369,
 '117': 5873,
 '118': 8764,
 '119': 8018,
 '12': 1170,
 '120': 9880,
 '121': 829,
 '122': 6120,
 '123': 3363,
 '124': 5067,
 '125': 384,
 '126': 7690,
 '127': 2390,
 '128': 5496,
 '129': 2722,
 '13': 2728,
 '130': 6883,
 '131': 5564,
 '132': 7751,
 '133': 758,
 '134': 1268,
 '135': 7325,
 '136': 423,
 '137': 724,
 '138': 7231,
 '139': 2438,
 '14': 2384,
 '140': 5804,
 '141': 5432,
 '142': 1704,
 '143': 627,
 '144': 3799,
 '145': 1341,
 '146': 4496,
 '147': 8495,
 '148': 7917,
 '149': 9466,
 '15': 8341,
 '150': 7852,
 '151': 1328,
 '152': 2329,
 '153': 3686,
 '154': 5837,
 '155': 4437,
 '156': 9780,
 '157': 7104,
 '158': 5988,
 '159': 7132,
 '16': 358,
 '160': 536,
 '161': 1663,
 '162': 6652,
 '163': 920

In [255]:
# title_raw_eucli={}
# title_raw_cosine={}

title_eucli={}
title_cosine={}

# for c in cluster_doc_rawdata.keys() : 
    
########Komoran
for c in cluster_doc.keys() :     


#     lines, vocab = doc_to_line(cluster_doc_rawdata[c], vocab)
    
########Komoran    
    lines, vocab = doc_to_line(cluster_doc[c], vocab)

    code = make_code(lines)

    code_cat=torch.cat(code,0)

    #code_feature extract(절대값 0.1미만 0으로)
#     code_cat_np = code_cat.data.numpy().squeeze()
#     temp = np.copy(code_cat_np)
#     temp[np.where(np.abs(temp)<feature_range)]=0
#     code_feature=torch.FloatTensor(temp).view(-1,300)

    #code 평균
    code_mean=torch.mean(code_cat,0).view(1,-1)

    #code 평균과 길이가 최소인 vector 구하기
    input1 = code_cat.data.numpy()
    mean_np = code_mean.data.numpy()
    eucli = euclidean_distances(input1, mean_np).squeeze()
    cosine = cosine_distances(input1, mean_np).squeeze()
        ############Komoran인 경우
        
    #{clusterno : title}
    title_eucli[c]=cluster_doc_rawdata[c][np.argmin(eucli)]
    title_cosine[c]=cluster_doc_rawdata[c][np.argmin(cosine)]

In [394]:
title_raw_cosine

{'0': '시원하다',
 '1': '맛이 깔끔해서',
 '10': '풍미가 좋아서',
 '100': '수입맥주이고 왠지 맛있을 것같은 이미지가 있다.  상표 발음이 멋지고 고급스러운 분위기다.',
 '101': '톡쏘는 느낌이 좋아서',
 '102': '달콤한 맛이 좋습니다',
 '103': '눈에 확 들어온다.',
 '104': '병이 세련되고 예뻐서, 강하지않아서',
 '105': '무겁지않고 상표이름대로 라이트해서.  먹기 편하다.',
 '106': '맛이 있고 내 취향에 맞아서',
 '107': '여러 종류의 맥주를 마셔보지는 않았지만, 그중에서는 가장 맛있었던 것 같습니다. 맥주는 일반적오로 약간 쌉쌀한 맛이 있는데 그런 것이 좀 덜하다고 느껴집니다. 친구들도 많이 마시고 그래서 부담없이 마시는 상표입니다.',
 '108': '라이트라는단어때문도있지만 시원하고 깜끔할것같은 기대감을갖게해서',
 '109': 'it has to be a heineken  맛이나 광고나...하이네켄 신봉자 입니다+_+',
 '11': '시원하고 깔끔합니다',
 '110': '카프리는맥주에 소주탄 맛이라 뭔가 맛있는 맛이라 좋아합니다  ',
 '111': '가장 보편적이라서',
 '112': '다른 맥주와 차별화 된 맛',
 '113': '홋카이도에서 삿포로 공장방문하여 먹었던 기억을 잊을수가없어서',
 '114': '습관적으로 먹는거라서',
 '115': '어릴적부터 익숙했고 맛이 부드럽다.  아니, 명칭을 호가든이라 읽을때 기분이 좋아서 일지도.',
 '116': '하정우가 좋아서',
 '117': '맥주의 색과 상표의 디자인이 잘 어우러져 있어서...',
 '118': '가장 기본적이고 대중적인느낌이라서',
 '119': '맥주가 목으로 넘어갈 때의 그 시원한 느낌이 좋다',
 '12': '자주 마셔서',
 '120': '여자들이 마시기 깔끔하다. 깔끔한게 가장 큰 장점인것 같다.  ',
 '121': '깔끔하고 맛있다. 그리고 주위에서 많이먹는다',
 '122': 

In [395]:
num_title_raw_cosine

{'0': 8828,
 '1': 9793,
 '10': 8171,
 '100': 1801,
 '101': 2692,
 '102': 4607,
 '103': 3590,
 '104': 4130,
 '105': 9936,
 '106': 4349,
 '107': 4731,
 '108': 5828,
 '109': 1529,
 '11': 1272,
 '110': 8082,
 '111': 9518,
 '112': 3193,
 '113': 8769,
 '114': 9721,
 '115': 9913,
 '116': 9803,
 '117': 584,
 '118': 375,
 '119': 5380,
 '12': 1170,
 '120': 5302,
 '121': 8266,
 '122': 5723,
 '123': 5590,
 '124': 8295,
 '125': 1916,
 '126': 2919,
 '127': 7710,
 '128': 3250,
 '129': 5759,
 '13': 2728,
 '130': 710,
 '131': 9322,
 '132': 1148,
 '133': 758,
 '134': 2499,
 '135': 10243,
 '136': 2595,
 '137': 9671,
 '138': 2148,
 '139': 6135,
 '14': 738,
 '140': 10086,
 '141': 5432,
 '142': 1704,
 '143': 9374,
 '144': 5941,
 '145': 186,
 '146': 8045,
 '147': 8495,
 '148': 7874,
 '149': 9466,
 '15': 3893,
 '150': 7852,
 '151': 1328,
 '152': 2329,
 '153': 6044,
 '154': 7638,
 '155': 4437,
 '156': 5382,
 '157': 3638,
 '158': 9135,
 '159': 7132,
 '16': 10148,
 '160': 967,
 '161': 8741,
 '162': 9914,
 '163':

In [189]:
title_raw_cosine

{0: '효과가 그다지..',
 1: '편하고 효과도 빠름',
 2: '생각보다 나아지는걸 못 느꼇다.',
 3: '큰 효과를 못봤고 일시적이다.',
 4: '휴대성이 좋고 효과도 좋았다',
 5: '신속한 효능',
 6: '코막힌것이 잘뚫린 느낌이고 시원해서',
 7: '뿌리고 자니까 증상이 완화되는 느낌이었음',
 8: '생각보다 효과가 오래지속되지 않았다',
 9: '눈이 띄는 효과는 모르겠다',
 10: '효과가 어느정도 있어서',
 11: '사용했을때 일시적이라도 코막힘이 완화되는 현상 때문에',
 12: '잠깐 시원하게뚫리는거 같지만 지속력은 없는거같다',
 13: '나름 효과가 있기때문에',
 14: '코에 뿌리고 난후 효과가 괜찮아서 사용하겠됐음.',
 15: '약효가 오래가고 부작용이 적은거같다',
 16: '효과가 즉효성이고 나한테 제일 잘맞아서',
 17: '효과가 좋은 편이다.',
 18: '뿌리기 전보다 숨쉬기 편해짐',
 19: '주변 지인 추천으로 사용하였는데 효과가 괜찮음.',
 20: '다른제품과 특별히 다른 점을 찾지 못했다.',
 21: '내성이 생기는 듯한 생각이 듭니다.',
 22: '코가뚤리는 느낌이 시웒하다',
 23: '코에 약간 자극이 있는것 같아서',
 24: '비염이 심한정도여서 큰효과를 기대하진 않았고 그렇게 느꼈다',
 25: '부작용없이 무난하게 사용중이며 빠르지는 않지만 증상이 완화되어서 만족한다.',
 26: '효과가 좋았으나 사용할 양이 부족',
 27: '코가 약간 조이는 느낌이 든다고 함.',
 28: '드라마틱한 효과는 없기 때문이다.',
 29: '사용하면 편안한 느낌이 한번씩 드는것같습니다',
 30: '혁신적인 제품이다',
 31: '그냥 의사가 처방해 줘서 사용해봄',
 32: '효과가 신속하게 나타나고, 지속력이 길어서 사용하기 편리하다',
 33: '뿌리면 목이 아픔',
 34: '효과는 잇는것도 같은데 그닥 신박하다는 느낌은 없어서',
 35: '가지고 다니기 편하고 즉각적인 효과가 

In [13]:
#euclidean title/ doclist / clusterNo / cosine title
df = pd.DataFrame([title_raw_eucli,cluster_doc_rawdata]).T
df['clusterNo'] = df.index
cosine_title=list(title_raw_cosine.values())
cosine_title
df[2]=cosine_title

In [256]:
########Komoran
#euclidean title/ doclist / clusterNo / cosine title
df = pd.DataFrame([title_eucli,cluster_doc]).T
df['clusterNo'] = df.index
cosine_title=list(title_cosine.values())
cosine_title
df[2]=cosine_title

In [12]:
df

0  \
0                               밝은느낌이다   
1                                  가볍고   
10                             목넘김이 좋다   
100                          대중적인느낌이라서   
100_1                           깔끔한 느낌   
100_2                      깔끔한 느낌이 들어서   
100_3                           맛이깔금하다   
100_4                       깨끗한 느낌이 든다   
101                       부드러운 거품과 목넘김   
102                               부드럽다   
103          일본 자전거 여행을 할 때 하루 여행을 마치고   
104                        글라스도 마음에 들고   
105                           시원한감이 있다   
106                                김연아   
107                             순한맛이라서   
108                          국화향이나는듯하고   
109                         맛과 향이 탁월하고   
11                             맛이 부드럽다   
110                             보통맥주보다   
110_1                       글씨체도 맘에 들고   
110_10                         맛이 담백해서   
110_11                       맛이 입맛에 맞고   
110_12                          이름이 좋다   
110_13                       가장 익숙한맛이다   
110_14                         맛이 색다르고   
110_15                         칼로리가적어서   
110_16                        광고도 재미있고   
110_17                    전용잔에 따라먹는 재미   
110_18                           호감이가서   
110_19                         대표브렌드라서   
...                                ...   
85          헌데 다른 맥주와는 달리 목넘김이 매우 부드럽고   
86                           맛이 진한거같아서   
87                            뒷맛이 개운하다   
88                               마실때마다   
89                              쓴맛이 적다   
9                             거품이 부드럽고   
90                            가격도 괜찮아서   
91                           주로마시던것이라서   
92                               가벼운느낌   
93                              시원한것같다   
94                                크림맥주   
94_1                             산뜻한느낌   
94_10                 연한걸 좋아하는 사람한테 좋다   
94_11                   특유의 맛과 향을 좋아한다   
94_12                            무겁지않고   
94_13                          맛이 뛰어나서   
94_14                  호가든 맥주를 좋아하기때문에   
94_2                             입에 맞다   
94_3                               순해서   
94_4                        맛있어서 좋아합니다   
94_5                               진한맛   
94_6                             시크한매력   
94_7                           향이 독특하고   
94_8                   개인적으로 좋아하는 맛이라서   
94_9    기네스는 병도 맛있지만 저는 흑생맥주를 특히 좋아합니다   
95                                부담없고   
96                               습관적으로   
97        국내 대표적인 맥주 하이트보다는 쫌더 세련되 보이고   
98                                 편하고   
99                                광고효과   

                                                        1 clusterNo  \
0       [신세대 느낌이 난다, 젊은 느낌, 이국적인 느낌이 있다, 톡쏘는 느낌이 좋음, 톡...         0   
1       [가볍지 않고, 가벼운 맥주맛이 좋다, 가볍게 먹기 좋음, 가볍지 않은 맛, 맛이 ...         1   
10      [목넘김이 좋다, 목 넘김이 좋고, 목넘김이 좋다, 목넘김이 좋고, 목넘김이 좋다,...        10   
100     [개운한 느낌이 들고, 맛의 느낌이 좋타, 깨끗한 느낌을 준다, 이름에서 오는 느낌...       100   
100_1   [맛이나 느낌이 시원한 느낌이 난다, 부드러운느낌이라서요, 깔끔한 느낌이다, 부드러...     100_1   
100_2   [깔끔한 디자인과 시원한 느낌이 듭니다, 깔끔한 느낌이 들어서, 깔끔한 느낌이 드는...     100_2   
100_3   [세련되었으며 도시적인 느낌이 있다, 언제 먹어도 깔금한 맛, 깔금한맛, 나서 깔금...     100_3   
100_4   [깨끗한 느낌이 들어서 좋다, 깨끗한 느낌이 든다, 부드러우며 깊은 느낌이 든다, ...     100_4   
101     [거품이 주는 부드러운 맛이 일품이기 때문입니다, 부드러운 거품과 독특한 맛, 처음...       101   
102     [맥주가 깔끔하고, 맥주가 깔끔하고, 깔끔하며 시원함, 깔끔함이 마음에 든다, 뒤끝...       102   
103     [생맥주를 먹을때 아주 내 입맛에 맞다, 음식과 같이 먹을 때 맛있어서, 다른 맥주...       103   
104     [글라스도 마음에 들고, 글씨체라든지 디자인이 마음에 들어서, 마음에 드는 색과 구...       104   
105     [맥주 맛과 상표가 잘 어울린다, 잘 어울린다, 주변의 베경이 잘 어울린다, 좋아하...       105   
106     [맥스의 맛이 제일 내입맛에 맞음, 김연아, 맥스 공장 견학 당시 맛봤던 그 맛이 ...       106   
107     [타 맥주에 비해 색이 진하다, 순한맛, 다른 맥주 회사에 비해 밍밍한 느낌이 덜 ...       107   
108     [상큼한 향, 보리향이 살짝 느껴지는게 좋아서, 호가든 특유의 향이 좋아서장미향, ...       108   
109     [거품이 풍부해서 맛과 향이 날아가지 않는다, 맛과 향, 맛과 향이 좋아서, 향과 ...       109   
11      [부드러운 맛, 맛이 부드럽다, 부드러운 맛, 부드러운 맛이 있고, 맛이 부드럽고,...        11   
110     [톡쏘는 시원한 맛 때문 입니다, 저번에 견학갔었는데 제일 깔끔하게 맥주 제조했었음...       110   
110_1   [디자인

In [14]:
#[[clusterno , doc, euclidean title, cosine title]]
rows = []
_ = df.apply(lambda row: [rows.append([row['clusterNo'],nn,row[0],row[2]]) 
                         for nn in row[1]], axis=1)

In [15]:
rows

[['0', '시원하다', '시원하다', '시원하다'],
 ['0', '시원한맛', '시원하다', '시원하다'],
 ['0', '시원', '시원하다', '시원하다'],
 ['0', 'ㅈ다른 것 보다 더 시원한 맛이 난다', '시원하다', '시원하다'],
 ['0', '병을 딸때 시원하게 펑하는 소리가 나고, 맛도 좋은 것 같다', '시원하다', '시원하다'],
 ['0', '시원하고 탁 쏘는 맛이 봏아서', '시원하다', '시원하다'],
 ['0', '시원함', '시원하다', '시원하다'],
 ['0', '시원해서', '시원하다', '시원하다'],
 ['0', '시원한 맛', '시원하다', '시원하다'],
 ['0', '맛이시원하다', '시원하다', '시원하다'],
 ['0', '시원함', '시원하다', '시원하다'],
 ['0', '시원한 맛', '시원하다', '시원하다'],
 ['0', '톡 쏘고 시원하다', '시원하다', '시원하다'],
 ['0', '쌉살함 깔금함 시원함', '시원하다', '시원하다'],
 ['0', '시원해서', '시원하다', '시원하다'],
 ['0', '시원하다', '시원하다', '시원하다'],
 ['0', '시원합', '시원하다', '시원하다'],
 ['0', '톡쏘는 맛이 시원함.', '시원하다', '시원하다'],
 ['0', '톡쏘는 맛이 있다 그리고 시원하다', '시원하다', '시원하다'],
 ['0', '시원하고 맛이좋다', '시원하다', '시원하다'],
 ['0', '시원한맛', '시원하다', '시원하다'],
 ['0', '시원한맛', '시원하다', '시원하다'],
 ['0', '시원해서', '시원하다', '시원하다'],
 ['0', '시원해요~', '시원하다', '시원하다'],
 ['0', '시원한 맛과 쌉싸름한 맛이 좋음', '시원하다', '시원하다'],
 ['0', '시원하다', '시원하다', '시원하다'],
 ['0', '시원함', '시원하다', '시원하다'],
 ['0', '시원하다', '시원하다', '시원하다'

In [16]:
# dataframe으로 생성
df_new = pd.DataFrame(rows, columns=['clusterNo','raw_docs','title_euclidean','title_cosine'])
df_new['docno']=li_docno
df_new

clusterNo                                           raw_docs  \
0            0                                               시원하다   
1            0                                               시원한맛   
2            0                                                 시원   
3            0                               ㅈ다른 것 보다 더 시원한 맛이 난다   
4            0                  병을 딸때 시원하게 펑하는 소리가 나고, 맛도 좋은 것 같다   
5            0                                   시원하고 탁 쏘는 맛이 봏아서   
6            0                                                시원함   
7            0                                               시원해서   
8            0                                              시원한 맛   
9            0                                             맛이시원하다   
10           0                                                시원함   
11           0                                              시원한 맛   
12           0                                          톡 쏘고 시원하다   
13           0                                        쌉살함 깔금함 시원함   
14           0                                               시원해서   
15           0                                               시원하다   
16           0                                                시원합   
17           0                                        톡쏘는 맛이 시원함.   
18           0                                 톡쏘는 맛이 있다 그리고 시원하다   
19           0                                          시원하고 맛이좋다   
20           0                                               시원한맛   
21           0                                               시원한맛   
22           0                                               시원해서   
23           0                                              시원해요~   
24           0                                  시원한 맛과 쌉싸름한 맛이 좋음   
25           0                                               시원하다   
26           0                                                시원함   
27           0                                               시원하다   
28           0                                            맛이 시원해서   
29           0                                               시원하다   
...        ...                                                ...   
8349        98  광고나 홍보를 통해 카스가 한국에서 가장 많이 마시는 맥주로 인식이 됨, 그리고 카...   
8350        98                   시원한 맛이 있고 광고를 통해서 많이 접하게 되어 친근하다   
8351        98                      많은 매체 광고를 통해 친숙한 이미지이며, 대중적이다   
8352        98  일단 대중적이고 구하기 쉽고 가격도 적정하고 맥주하면 늘 하이트만 왠지 손에 자주갑...   
8353        98  광고를 통해 눈에 익은것도 있고 자주 마시기때문에 상표를 봤을때 친근하고 좋은느낌으...   
8354        98                                           광고를통해친숙함   
8355        98    맛이 입에맞고,  광고 등의 이미지를 통해서 깔끔함고 상쾌한 느낌이 들어서 좋아한다.   
8356        98                       맛이 가볍고 깔끔함. 광고를 통해 재미있는 이미지.   
8357        98  광고등을 통해 가장 친근한 이미지가 있고 맥주 맛도 여타 맥주들에 비해 쉬원한 느낌...   
8358        98                           맥주의 맛 자체가 여타 브랜드 보다 탁월하다   
8359        98              맛이 깔끔해서   광고 등을 통해 자주 접하다보니 친근한 느낌이라서   
8360        98  대중적인맛과 광고의 효과도 무의식적으로 내게 많은 긍정의 영향을 주었다고 말할수 있겠다.   
8361        98                           광고도 재미있고 맛도 가벼워서 즐기기에 좋다   
8362        98  처음 입에 닿는 거품이 부드럽고  잡내가 없으며 맥주 맛이 깔끔하여 목넘김이 좋습니...   
8363        99               거품이 풍부하고 부드러우며, 광고또한 매우 매력적이어서 끌립니다.   
8364        99                       부드럽고 거품이풍부하며, 뒷맛이 씁쓸한 것이 좋아서   
8365        99                                 목넘김이 부드럽고 거품이 풍부해서   
8366        99                          톡쏘는 정도가 적당하고 풍부하고 부드러운 커품   
8367        99                     탄산 쏘는맛이랑 보리맛이 적절히 제입맛에 맞는것같아요.   
8368        99                                풍부한 거품과 부드러운 맛, 엔젤링   
8369        99  삿포르를 20대 초반 중국에 여행 가서 처음 마셔 보았는데 아주 풍부한 거품과 부드...   
8370        99                              탄산이 없어 부드럽고 보리맛이 풍부해서   
8371        99                                과일 향과 거품이 풍부하고 부드러움   
8372        99                       호가든의 풍부한 거품의 맛이 부드럽고 목넘김에 좋다   
8373        99      다른 맥주에 비해서 거품도 풍부하며, 마실때의 목넘김이 부드러운것같고 쓴맛이 적다   
8374        99             국산중에서 가장 탄산이 살아있는 느낌과    보리의 풍부한 향이 좋다   
837

In [261]:
# 각 doc별 euclidean과 cosine에 대한 title csv 생성
df_new.to_csv('1207_med_komoran_center_vector_title_400.csv',sep=',',encoding='CP949')

# Parsing data

In [17]:
# load_path='output/out1102'
# load_path='output/out_twitter1103'
# load_path='output/out1106_komoran'
load_path='output/outparsing1204'
# load_path='output/output1207_newdata2'
# load_path='output/output1207_newdata_komoran'

In [18]:
idx2word, autoencoder, gan_gen, gan_disc, word2idx= load_models_decode(load_path)

Loading models fromoutput/outparsing1204


In [8]:
# vocab2=idx2word
# vocab2
# word2idx

{0: '<pad>',
 1: '<sos>',
 2: '<eos>',
 3: '<oov>',
 4: '가',
 5: '가.',
 6: '가가',
 7: '가거나',
 8: '가게',
 9: '가게가도',
 10: '가게나',
 11: '가게되면',
 12: '가게되었으며',
 13: '가게마다',
 14: '가게에',
 15: '가게에서',
 16: '가게에서나',
 17: '가게주인이주어서.',
 18: '가격',
 19: '가격.',
 20: '가격과',
 21: '가격까지',
 22: '가격대',
 23: '가격대가',
 24: '가격대가있지만',
 25: '가격대도',
 26: '가격대로',
 27: '가격대비',
 28: '가격대에',
 29: '가격대와',
 30: '가격대중성.',
 31: '가격도',
 32: '가격도싸고',
 33: '가격면에서',
 34: '가격보다도',
 35: '가격부담없이',
 36: '가격에',
 37: '가격에다',
 38: '가격에서',
 39: '가격은',
 40: '가격을',
 41: '가격이',
 42: '가격이랑',
 43: '가격이싸고',
 44: '가격저렴.',
 45: '가격저렴하고',
 46: '가격적으로나',
 47: '가격적으로도',
 48: '가격적인',
 49: '가격차이',
 50: '가격치곤',
 51: '가고',
 52: '가공공법',
 53: '가기',
 54: '가까운',
 55: '가까운데서',
 56: '가까운맛.',
 57: '가까움',
 58: '가까움.',
 59: '가까이서',
 60: '가까이에서',
 61: '가깝게',
 62: '가깝다고',
 63: '가끔',
 64: '가끔가다',
 65: '가끔식',
 66: '가끔씩',
 67: '가나',
 68: '가는',
 69: '가는거같다.',
 70: '가는구간에도',
 71: '가는데',
 72: '가는듯한',
 73: '가능.',
 74: '가능하고',
 75: '가능하다',
 76: '가능하다.',
 77: '가능하며

In [19]:
path_raw = 'codedata/1207basic/DBSCAN_result_Topic_refined_Parsed.csv'
maxlen=100

In [20]:
data = pd.read_csv(path_raw, names = None,encoding='cp949')
clusternum=data['clusterno']
docno = data['docNo']
doc = data['raw_doc']

In [236]:
################Komoran 단위
from konlpy.tag import Komoran

pos_tagger = Komoran()

def tokenize_komoran(doc):
    # norm, stem은 optional
    return [x for x, t in pos_tagger.pos(doc)]

token = []
for row in doc :
    token.append(' '.join(k for k in tokenize_komoran(row)))

data['raw_doc']= pd.DataFrame(token)[0]
tokendoc = data['raw_doc']

data

clusterno  Unnamed: 1  docNo  \
0            0           0   1024   
1            0           1   1666   
2            0           2   1155   
3            0           3    388   
4            0           4   2438   
5            0           5    449   
6            0           6    393   
7            0           7    780   
8            0           8   1172   
9            0           9   1173   
10           0          10   1292   
11           0          11    665   
12           0          12    137   
13           0          13    516   
14           0          14    157   
15           0          15   1182   
16           0          16    287   
17           0          17   1189   
18           0          18   2728   
19           0          19    541   
20           0          20   1011   
21           0          21   1054   
22           0          22   2359   
23           0          23   2783   
24           0          24     61   
25           0          25   1472   
26           0          26     65   
27           0          27    211   
28           0          28     73   
29           0          29   1719   
..         ...         ...    ...   
654         13         503   2547   
655         13         504   1974   
656         13         505    841   
657         13         506   1600   
658         13         507   1979   
659         13         508    958   
660         13         509   1983   
661         13         510    960   
662         13         511    961   
663         13         512   1987   
664         13         513   1014   
665         13         514    971   
666         13         515    977   
667         13         516   2211   
668         13         517    980   
669         13         518    982   
670         13         519   2554   
671         13         520   2021   
672         13         521   1363   
673         13         522   2029   
674         13         523   1006   
675         13         524   1008   
676         13         525   2033   
677         13         526    859   
678         13         527   1350   
679         13         528   1015   
680         13         529   1016   
681         13         530   1017   
682         13         531   1020   
683         13         532   1023   

                                               raw_doc  
0                                           효과 가 아 있 다  
1                                        효과 가 아 그다지 ..  
2                                               효과 있 다  
3                                          효과 가 아 있 어서  
4                                          효과 가 아 있 어서  
5                                                효과 별로  
6                                           효과 가 아 좋 다  
7                                         효과 가 아 있 으니까  
8                                   효과 가 아 그리 좋 지 않 아서  
9                       효과 가 아 바로 오 아 닿 지 가 아 않 늘 ㄴ다 .  
10                                          효과 가 아 좋 다  
11                                          효과 가 아 있 다  
12                                         효과 가 아 좋 아서  
13                                          효과 가 아 좋 음  
14                                           효과 가 아 별로  
15                                         효과 가 아 좋 아서  
16                               크 ㄴ 효과 늘 ㄴ 아직 잘 모르겠ㄸ다  
17                                          효과 가 아 좋 음  
18                                          효과 가 아 좋 다  
19                                          효과 가 아 좋 다  
20                                         효과 가 아 좋 아서  
21                                      효과 를 보 오 았 다 .  
22                                       효과 가 아 딱히 없 음  
23                                              효과 좋 음  
24                                          효과 가 아 좋 다  
25                                          효과 가 아 좋 음  
26                                          효과 가 아 좋 다  
27                                          효과 가 아 좋 다  
28                                         효과 가 아 좋 아서  


In [21]:
# {clusterno : [doc]}
parse_groupby_cluster = doc.groupby([clusternum])
parse_cluster_doc_rawdata=parse_groupby_cluster.apply(lambda x: x.tolist()).to_dict()
# dbscan 노이즈 결과 버리기
del parse_cluster_doc_rawdata['-1']

    
# {clusterno : [docno]}
parse_docno_groupby_cluster = docno.groupby([clusternum])
parse_docno_cluster=parse_docno_groupby_cluster.apply(lambda x: x.tolist()).to_dict()
# dbscan 노이즈 결과 버리기
del parse_docno_cluster['-1']

In [242]:
parse_docno_cluster

{'0': ['6980_1',
  '8990',
  '1606_2',
  '10239',
  '2514',
  '1774',
  '5684_5',
  '124_2',
  '8015',
  '8360_1',
  '6452',
  '4776',
  '5150',
  '8019_0',
  '1239_1',
  '1024_1',
  '7341',
  '9318_2',
  '3898_1',
  '5586',
  '3957_1',
  '6919_1',
  '3838_1',
  '8040_2',
  '4453',
  '6857',
  '818_1',
  '4747_2',
  '437_1',
  '2195',
  '2777_0',
  '8734_2',
  '7886_1',
  '4167_3',
  '9841_1',
  '485_0',
  '2_1',
  '1566',
  '7169_1',
  '7896',
  '8311_1',
  '7865_1',
  '2795',
  '328',
  '720_1',
  '5384',
  '6061_0',
  '6384_1',
  '6861',
  '1886',
  '2346',
  '8183_0',
  '7073_0',
  '1580',
  '7308',
  '3289_1',
  '489_1'],
 '1': ['6734_0',
  '6402',
  '9198_1',
  '5449',
  '10140_0',
  '3484',
  '9500',
  '2790_0',
  '1082_0',
  '3026_1',
  '5749_1',
  '7280_0',
  '5542',
  '6356',
  '4726_0',
  '1883_1',
  '6662_2',
  '7981_0',
  '5142_0',
  '3930_0',
  '6386_0',
  '2908',
  '6975_0',
  '4771',
  '1410_2',
  '5048_1',
  '1168',
  '8042_1',
  '8073_1',
  '1517_1',
  '4846_1',
  '11

In [30]:
#마지막 결과표에 쓰기 위해 모든 docno를 순서대로 하나의 리스트로
li_docno=list(parse_docno_cluster.values())
li_docno = list(chain.from_iterable(li_docno))
len(li_docno)

13910

In [238]:
##########Komoran
groupby_cluster_token = tokendoc.groupby([clusternum])
cluster_doc=groupby_cluster_token.apply(lambda x: x.tolist()).to_dict()
if '-1' in cluster_doc.keys():
    del cluster_doc['-1']

In [181]:
cluster_doc_rawdata

{0: ['큰 효과를 보지는 못함.',
  '효과',
  '효과가 바로 와닿지가 않는다.  \r\n\r\n',
  '효과가 그다지..',
  '효과가 좋다',
  '신속셩 효과',
  '효과없음',
  '효과가 있다',
  '효과가 좋아서',
  '효과가좋다',
  '효과가있다',
  '효과가 신속하게 나서',
  '효과가 있었다',
  '즉시효과',
  '효과를 봤다.',
  '효과가 좋았었다',
  '효과가 좋다',
  '효과좋음',
  '신속한 효과',
  '효과가 신속함',
  '효과가 있으니까',
  '효과가 좋기떄문에',
  '효과가좋다',
  '효과가 있다',
  '큰 효과가 없었음',
  '효과가 좋았음',
  '효과가 좋았다.',
  '효과가 좋다',
  '효과가 그리 좋지 않아서',
  '효과가 딱히 없음',
  '효과적임',
  '효과있어서',
  '효과가 신속함',
  '신속하고 효과적임',
  '효과가 좋아서',
  '효과가 좋아서',
  '효과가 좋아서',
  '효과 별로',
  '효과가 좋아서',
  '효과가 있어서',
  '효과가 좋다',
  '효과가 있음',
  '큰효과는 아직 잘 모르겠ㄸ다',
  '효과가 있어서',
  '크게 효과를 보지 못해서',
  '효과있다',
  '효과가 좋다',
  '신속한 효과',
  '효과가 신속',
  '효과가 좋다',
  '효과가 있어서',
  '효과가 좋음',
  '효과좋음',
  '효과가 별로',
  '효과가 좋음',
  '효과가 별로',
  '효과가 좋음'],
 1: ['효과가 빠르다',
  '사용 편리성과 빠른 효과,효능 때문에',
  '효과가 빠름',
  '편리성 지속성',
  '효과가 빠른 편이다',
  '효과가 빠르다',
  '효과가 빠르고 진정이 잘 되서',
  '효과가 지속되지않아서',
  '사용할 때 효과가 빠르게 나타나서',
  '효과가 빠르다',
  '편하고 효과도 빠름',
  '효과가 바로 나타난다',
  '효과가 빠르다',
  '바로 효과가 나타나서',
  '효과가 빠름

In [22]:
vocab = word2idx
ntokens = len(vocab)

def doc_to_line(cluster_doc, vocab):

    dropped = 0
    linecount = 0
    lines = []
    for line in cluster_doc:
        linecount += 1        
#         if self.lowercase:
#             words = line[:-1].lower().strip().split(" ")
#         else:
#             words = line[:-1].strip().split(" ")
        words = line[:-1].strip().split(" ")
        
        if len(words) > maxlen:
            dropped += 1
            continue
        words = ['<sos>'] + words
        words += ['<eos>']

        # vectorize

        unk_idx = vocab['<oov>']
        indices = [vocab[w] if w in vocab else unk_idx for w in words]

#         print(indices)
        lines.append(indices)
        
    return lines, vocab

In [23]:
def make_code(lines):
    eval_batch_size = 1
    test_data = batchify(lines, eval_batch_size, shuffle=False)
     
    code = []
    for i, batch in enumerate(test_data):
            source, target, lengths = batch
    #         source = to_gpu(True, Variable(source, volatile=True))
    #         target = to_gpu(True, Variable(target, volatile=True))
    #         mask = target.gt(0)
    #         masked_target = target.masked_select(mask)
    #         # examples x ntokens
    #         output_mask = mask.unsqueeze(1).expand(mask.size(0), ntokens)

            # output: batch x seq_len x ntokens
            output = autoencoder.encode(Variable(source), lengths, noise=False)
#             print(output)
            code.append(output)
    return code

In [24]:
parse_title_raw_eucli={}
parse_title_raw_cosine={}

parse_num_title_raw_eucli={}
parse_num_title_raw_cosine={}
# title_eucli={}
# title_cosine={}

for c in parse_cluster_doc_rawdata.keys() : 
    
########Komoran
# for c in cluster_doc.keys() :     


    lines, vocab = doc_to_line(parse_cluster_doc_rawdata[c], vocab)
    
########Komoran    
#     lines, vocab = doc_to_line(cluster_doc[c], vocab)

    code = make_code(lines)

    code_cat=torch.cat(code,0)

    #code_feature extract(절대값 0.1미만 0으로)
#     code_cat_np = code_cat.data.numpy().squeeze()
#     temp = np.copy(code_cat_np)
#     temp[np.where(np.abs(temp)<feature_range)]=0
#     code_feature=torch.FloatTensor(temp).view(-1,300)

    #code 평균
    code_mean=torch.mean(code_cat,0).view(1,-1)

    #code 평균과 길이가 최소인 vector 구하기
    input1 = code_cat.data.numpy()
    mean_np = code_mean.data.numpy()
    eucli = euclidean_distances(input1, mean_np).squeeze()
    cosine = cosine_distances(input1, mean_np).squeeze()
    
    #{clusterno : title}
    parse_title_raw_eucli[c]=parse_cluster_doc_rawdata[c][np.argmin(eucli)]
    parse_title_raw_cosine[c]=parse_cluster_doc_rawdata[c][np.argmin(cosine)]

    #{clusterno : title docno}
    parse_num_title_raw_eucli[c]=parse_docno_cluster[c][np.argmin(eucli)]
    parse_num_title_raw_cosine[c]=parse_docno_cluster[c][np.argmin(cosine)]
    
    ############Komoran인 경우
#     title_eucli[c]=cluster_doc_rawdata[c][np.argmin(eucli)]
#     title_cosine[c]=cluster_doc_rawdata[c][np.argmin(cosine)]

In [255]:
# title_raw_eucli={}
# title_raw_cosine={}

title_eucli={}
title_cosine={}

# for c in cluster_doc_rawdata.keys() : 
    
########Komoran
for c in cluster_doc.keys() :     


#     lines, vocab = doc_to_line(cluster_doc_rawdata[c], vocab)
    
########Komoran    
    lines, vocab = doc_to_line(cluster_doc[c], vocab)

    code = make_code(lines)

    code_cat=torch.cat(code,0)

    #code_feature extract(절대값 0.1미만 0으로)
#     code_cat_np = code_cat.data.numpy().squeeze()
#     temp = np.copy(code_cat_np)
#     temp[np.where(np.abs(temp)<feature_range)]=0
#     code_feature=torch.FloatTensor(temp).view(-1,300)

    #code 평균
    code_mean=torch.mean(code_cat,0).view(1,-1)

    #code 평균과 길이가 최소인 vector 구하기
    input1 = code_cat.data.numpy()
    mean_np = code_mean.data.numpy()
    eucli = euclidean_distances(input1, mean_np).squeeze()
    cosine = cosine_distances(input1, mean_np).squeeze()
        ############Komoran인 경우
        
    #{clusterno : title}
    title_eucli[c]=cluster_doc_rawdata[c][np.argmin(eucli)]
    title_cosine[c]=cluster_doc_rawdata[c][np.argmin(cosine)]

In [193]:
title_eucli

{0: '효과가 좋기떄문에',
 1: '효과가 빨라서',
 2: '먹는약보다 효과가 없는것 같다. 뿌리는 기구가 잘 망가진다',
 3: '일시적이라서',
 4: '사용후에 효과가 좋음',
 5: '보통임',
 6: '시원',
 7: '증상이 심할 때만 사용하였고 사용 후 바로 취침에 들어서 정확한 효능을 모른다',
 8: '지속성과 신속성이 있으며, 코가 잘 뚫린다.',
 9: '모름',
 10: '그럭저럭 괜찮았다.',
 11: '효과가 잘나올때도 있고 아닐때도있어서',
 12: '지속력이 오래 간다',
 13: '대체로 무난함',
 14: '코에뿌리면 약품이 흘러 불편함',
 15: '체질',
 16: '제 질환이 만성이라서 약간의 도움만 받았을 뿐입니다.',
 17: '효과있는편',
 18: '순간적',
 19: '주변지인들이 사용해서 써보니 나쁘지 않다 오트리빈과 같은 느낌이라 쓸만하다',
 20: '다른 스프레이 제품과 비교하여 좋은 점이 없음',
 21: '증세완화뿐 사용하지않으면 다시 증상생김',
 22: '코액 스프레이헤두 뻥뚤리는 느낌이 없. 코가 아플때두 있구...',
 23: '코에 자극이 강한느낌이 들어서',
 24: '비염이 심한정도여서 큰효과를 기대하진 않았고 그렇게 느꼈다',
 25: '예전에 사용해봤을 때는 쓰다는 느낌만 강함',
 26: '의사가 유명한거라고 추천해줘서 지금까지 쓰고있고 잘 듣는편이다',
 27: '코 막힐때 뚫어줬었지만 자주 목으로 넘어갔었음',
 28: '특별히 드라마틱한 효과를 보지 못해서',
 29: '코가 막혀서 잠자기 불편할때 코가 뚤려서 편함 하지만 목으로 액이 넘어서와서 불편함으로 만족하는편',
 30: '이유없음',
 31: '진료 당시 의사가 처방해 주었으며, 처방 해준 스프레이가 효과가 있었기 때문에 추후에도 계속 처방을 요구 했음',
 32: '효과는 나쁘지 않았으나 증상이 자주 나타나 많이 써야했기 때문에',
 33: '뿌리면 목이 아픔',
 34: '효과와 지속성 둘 다 그닥 나쁜편이 아니

In [189]:
title_raw_cosine

{0: '효과가 그다지..',
 1: '편하고 효과도 빠름',
 2: '생각보다 나아지는걸 못 느꼇다.',
 3: '큰 효과를 못봤고 일시적이다.',
 4: '휴대성이 좋고 효과도 좋았다',
 5: '신속한 효능',
 6: '코막힌것이 잘뚫린 느낌이고 시원해서',
 7: '뿌리고 자니까 증상이 완화되는 느낌이었음',
 8: '생각보다 효과가 오래지속되지 않았다',
 9: '눈이 띄는 효과는 모르겠다',
 10: '효과가 어느정도 있어서',
 11: '사용했을때 일시적이라도 코막힘이 완화되는 현상 때문에',
 12: '잠깐 시원하게뚫리는거 같지만 지속력은 없는거같다',
 13: '나름 효과가 있기때문에',
 14: '코에 뿌리고 난후 효과가 괜찮아서 사용하겠됐음.',
 15: '약효가 오래가고 부작용이 적은거같다',
 16: '효과가 즉효성이고 나한테 제일 잘맞아서',
 17: '효과가 좋은 편이다.',
 18: '뿌리기 전보다 숨쉬기 편해짐',
 19: '주변 지인 추천으로 사용하였는데 효과가 괜찮음.',
 20: '다른제품과 특별히 다른 점을 찾지 못했다.',
 21: '내성이 생기는 듯한 생각이 듭니다.',
 22: '코가뚤리는 느낌이 시웒하다',
 23: '코에 약간 자극이 있는것 같아서',
 24: '비염이 심한정도여서 큰효과를 기대하진 않았고 그렇게 느꼈다',
 25: '부작용없이 무난하게 사용중이며 빠르지는 않지만 증상이 완화되어서 만족한다.',
 26: '효과가 좋았으나 사용할 양이 부족',
 27: '코가 약간 조이는 느낌이 든다고 함.',
 28: '드라마틱한 효과는 없기 때문이다.',
 29: '사용하면 편안한 느낌이 한번씩 드는것같습니다',
 30: '혁신적인 제품이다',
 31: '그냥 의사가 처방해 줘서 사용해봄',
 32: '효과가 신속하게 나타나고, 지속력이 길어서 사용하기 편리하다',
 33: '뿌리면 목이 아픔',
 34: '효과는 잇는것도 같은데 그닥 신박하다는 느낌은 없어서',
 35: '가지고 다니기 편하고 즉각적인 효과가 

In [26]:
#euclidean title/ doclist / clusterNo / cosine title
df = pd.DataFrame([parse_title_raw_eucli,parse_cluster_doc_rawdata]).T
df['clusterNo'] = df.index
cosine_title=list(parse_title_raw_cosine.values())
cosine_title
df[2]=cosine_title

In [75]:
df

0  \
0                               느낌이 좋다   
1                                  가볍고   
10                             목넘김이 좋다   
100_1                           깔끔한 느낌   
100_2                       깔끔한 느낌이 좋다   
100_3                             깔금한맛   
100_4                       깨끗한 느낌이 든다   
101                       부드러운 거품과 목넘김   
102                     프리미엄 몰츠맛이 깔끔해서   
103                   일본 갔을 때 생맥주에 반했다   
104                      발적회수가 마음에 들었고   
105                       분위기가 나랑 어울리고   
106                                김연아   
107                     다른 맥주에 비해 순한 맛   
108                              향이 풍미   
109                           맛과 향이 좋고   
11                             맛이 부드럽다   
110_1                       선전이 맘에 들어서   
110_10                         맛이 담백해서   
110_11                      맛이 입맛에 맞아서   
110_12                         이름이 재밋다   
110_13                       가장 익숙한맛이다   
110_14                         맛이 색다르고   
110_15                         칼로리가적어서   
110_16                        광고도 재미있고   
110_17                     전용잔에 먹는게 좋다   
110_18                           호감이가서   
110_19                         대표브렌드라서   
110_2                             광고모델   
110_20                        맛이 하이트보다   
...                                ...   
84                       레몬을 넣어먹는게 맛있고   
85                 다른 맥주와 달리 목넘김이 부드럽고   
86                           맛이 진한거같아서   
87                            뒷맛이 개운하다   
88                       마실때 실제로도 시원하고   
89                              쓴맛이 적다   
9                             거품이 부드럽고   
90                             가격이 착하다   
91                           주로마시던것이라서   
92                           가볍게 즐길수잇음   
93                              시원한것같다   
94_1                             산뜻한느낌   
94_10                 연한걸 좋아하는 사람한테 좋다   
94_11                   특유의 맛과 향을 좋아한다   
94_12                            무겁지않고   
94_13                          맛이 뛰어나서   
94_14               그 후로 호가든을 좋아하게 되었다   
94_2                         맛이 입에 맞아서   
94_3                               순해서   
94_4                        맛있어서 좋아합니다   
94_5                               진한맛   
94_6                             시크한매력   
94_7                           향이 독특하고   
94_8                         개인적으로 좋아함   
94_9    기네스는 병도 맛있지만 저는 흑생맥주를 특히 좋아합니다   
95                                부담없고   
96                            예전부터 먹었다   
97                        국내 맥주 중 세련되고   
98                                 편하고   
99                                광고효과   

                                                        1 clusterNo  
0       [신세대 느낌이 난다, 젊은 느낌, 이국적인 느낌이 있다, 톡쏘는 느낌이 좋음, 톡...         0  
1       [가볍지 않고, 가벼운 맥주맛이 좋다, 가볍게 먹기 좋음, 가볍지 않은 맛, 맛이 ...         1  
10      [목넘김이 좋다, 목 넘김이 좋고, 목넘김이 좋다, 목넘김이 좋고, 목넘김이 좋다,...        10  
100_1   [맛이나 느낌이 시원한 느낌이 난다, 부드러운느낌이라서요, 깔끔한 느낌이다, 부드러...     100_1  
100_2   [깔끔한 디자인과 시원한 느낌이 듭니다, 깔끔한 느낌이 들어서, 깔끔한 느낌이 드는...     100_2  
100_3   [세련되었으며 도시적인 느낌이 있다, 언제 먹어도 깔금한 맛, 깔금한맛, 나서 깔금...     100_3  
100_4   [깨끗한 느낌이 들어서 좋다, 깨끗한 느낌이 든다, 부드러우며 깊은 느낌이 든다, ...     100_4  
101     [거품이 주는 부드러운 맛이 일품이기 때문입니다, 부드러운 거품과 독특한 맛, 처음...       101  
102     [맥주가 깔끔하고, 맥주가 깔끔하고, 깔끔하며 시원함, 깔끔함이 마음에 든다, 뒤끝...       102  
103     [생맥주를 먹을때 아주 내 입맛에 맞다, 음식과 같이 먹을 때 맛있어서, 다른 맥주...       103  
104     [글라스도 마음에 들고, 글씨체라든지 디자인이 마음에 들어서, 마음에 드는 색과 구...       104  
105     [맥주 맛과 상표가 잘 어울린다, 잘 어울린다, 주변의 베경이 잘 어울린다, 좋아하...       105  
106     [맥스의 맛이 제일 내입맛에 맞음, 김연아, 맥스 공장 견학 당시 맛봤던 그 맛이 ...       106  
107     [타 맥주에 비해 색이 진하다, 순한맛, 다른 맥주 회사에 비해 밍밍한 느낌이 덜 ...       107  
108     [상큼한 향, 보리향이 살짝 느껴지는게 좋아서, 호가든 특유의 향이 좋아서장미향, ...       108  
109     [거품이 풍부해서 맛과 향이 날아가지 않는다, 맛과 향, 맛과 향이 좋아서, 향과 ...       109  
11      [부드러운 맛, 맛이 부드럽다, 부드러운 맛, 부드러운 맛이 있고, 맛이 부드럽고,...        11  
110_1   [디자인 컬러 광고가 맘에 들었고, 그냥 병색도 맘에들고, 맛도 맘에들고, 이름이 ...     110_1  
110_10  [담백한 맛, 담백한맛, 맛이 담백해서, 맛이담백하다, 맛이 담백, 담백한 맛, 맛...    110_10  
110_11  [맛이 입맛에 맞고, 맛이 입맛에 맞아서, 

In [256]:
########Komoran
#euclidean title/ doclist / clusterNo / cosine title
df = pd.DataFrame([title_eucli,cluster_doc]).T
df['clusterNo'] = df.index
cosine_title=list(title_cosine.values())
cosine_title
df[2]=cosine_title

In [ ]:
df

In [27]:
#[[clusterno , doc, euclidean title, cosine title]]
rows = []
_ = df.apply(lambda row: [rows.append([row['clusterNo'],nn,row[0],row[2]]) 
                         for nn in row[1]], axis=1)

In [28]:
rows

[['0', '신세대 느낌이 난다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '젊은 느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '이국적인 느낌이 있다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '톡쏘는 느낌이 좋음', '느낌이 좋다', '느낌이 좋다'],
 ['0', '톡 쏘는 느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '느낌이 좋다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '밝은느낌이다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '깔금하고', '느낌이 좋다', '느낌이 좋다'],
 ['0', '신비로운느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '깔금하다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '고품격 같은 느낌이 들어서 입니다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '느낌이좋아서', '느낌이 좋다', '느낌이 좋다'],
 ['0', '왠지 젊은 느낌이 들어서', '느낌이 좋다', '느낌이 좋다'],
 ['0', '젊은 느낌이 나고', '느낌이 좋다', '느낌이 좋다'],
 ['0', '젊은 느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '맑은느낌이라 좋음', '느낌이 좋다', '느낌이 좋다'],
 ['0', '젊은 느낌이라서', '느낌이 좋다', '느낌이 좋다'],
 ['0', '도시적인 느낌이 들어 좋다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '남들과 다른 느낌을 주어서', '느낌이 좋다', '느낌이 좋다'],
 ['0', '느낌이 좋음', '느낌이 좋다', '느낌이 좋다'],
 ['0', '느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '상콤한 느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '젊은 느낌', '느낌이 좋다', '느낌이 좋다'],
 ['0', '그런 느낌입니다', '느낌이 좋다', '느낌이 좋다'],
 ['0', '보기만해도 톡쏘는 느낌이 전해져서 좋다', '느낌이 좋다'

In [31]:
# dataframe으로 생성
df_new_parsing = pd.DataFrame(rows, columns=['clusterNo','raw_docs','title_euclidean','title_cosine'])
df_new_parsing['docno']=li_docno
df_new_parsing

clusterNo                                           raw_docs  \
0             0                                         신세대 느낌이 난다   
1             0                                              젊은 느낌   
2             0                                        이국적인 느낌이 있다   
3             0                                         톡쏘는 느낌이 좋음   
4             0                                            톡 쏘는 느낌   
5             0                                             느낌이 좋다   
6             0                                             밝은느낌이다   
7             0                                               깔금하고   
8             0                                             신비로운느낌   
9             0                                               깔금하다   
10            0                                 고품격 같은 느낌이 들어서 입니다   
11            0                                             느낌이좋아서   
12            0                                      왠지 젊은 느낌이 들어서   
13            0                                          젊은 느낌이 나고   
14            0                                              젊은 느낌   
15            0                                          맑은느낌이라 좋음   
16            0                                           젊은 느낌이라서   
17            0                                     도시적인 느낌이 들어 좋다   
18            0                                     남들과 다른 느낌을 주어서   
19            0                                             느낌이 좋음   
20            0                                                 느낌   
21            0                                             상콤한 느낌   
22            0                                              젊은 느낌   
23            0                                           그런 느낌입니다   
24            0                              보기만해도 톡쏘는 느낌이 전해져서 좋다   
25            0                                               깔금하다   
26            0                                          싶은 느낌이 든다   
27            0                                         좋은느낌으로 다가옴   
28            0                                             좋은느낌이다   
29            0                                        빈티지한 느낌이 좋다   
...         ...                                                ...   
13880        99                              다른 맥주에 비해 톡 쏘는 맛이 강하고   
13881        99                                   저렴하면서 탄산이 강하지 않고   
13882        99                                             강하지 않다   
13883        99                                       향이 강하지 않아 좋다   
13884        99                                         향이 강하지 않아서   
13885        99                                          시원함 광고의효과   
13886        99          탄산의 느낌이 가장 강하게 느껴져서요 갈증이 풀리는 느낌이 다른 맥주들보다   
13887        99                               넘어가면서 휘저어 놓는 느낌이 강하다   
13888        99                                           광고효과가 크다   
13889        99                                             강하지 않다   
13890        99             나온지 얼마되지 않은 신제품으로 싸이 광고효과와 더불어 급속도로 뜨고   
13891        99                                        톡쏘는 느낌이 강하다   
13892        99                                   맥주 맛이 독특함 풍미가 강함   
13893        99                                           청량감이 강하다   
13894        99                                               광고효과   
13895        99                                 드라이한 느낌이 강해서 달지 않고   
13896        99                                 일단은 TV광고효과를 많이본듯하다   
13897        99                                   살짝 강한듯하면서 쓴맛이 좋다   
13898        99                                      광고의 효과가 큰것 같다   
13899        99                 우선 다른 맥주들에 비해서 티비광고의 효과가 컷던 것 같습니다   
13900        99                                 칼로리 조절에 효과적일 것 같아서   
13901        99                                       한국적인 느낌이 강해서   
13902        99                                     알콜의 잡내가 강하지 않다   
13903        99                                   다른 맥주에 비해 맛이 강하다   
13904        99                                     알콜의 느낌이 강하지 않다   
13905        99 

In [261]:
# 각 doc별 euclidean과 cosine에 대한 title csv 생성
df_new_parsing.to_csv('1207_med_komoran_center_vector_title_400.csv',sep=',',encoding='CP949')

# Parsing data Title

In [45]:
parseno=df_new_parsing['docno']
title=df_new_parsing['title_cosine']
myzip = zip(parseno, title)
result_doc_cosine = dict(myzip)
len(result_doc_cosine)

parseno=df_new_parsing['docno']
title=df_new_parsing['title_euclidean']
myzip = zip(parseno, title)
result_doc_euclidean = dict(myzip)
len(result_doc_euclidean)

13910

In [42]:
parseno=df_new_parsing['docno']
cluster=df_new_parsing['clusterNo']
myzip = zip(parseno, cluster)
number = dict(myzip)
keys = natsort.natsorted(number.keys())
number = collections.OrderedDict((k, number[k]) for k in keys)

In [43]:
number

OrderedDict([('2_0', '113'),
             ('2_1', '0'),
             ('3', '16'),
             ('4', '121'),
             ('5_0', '148'),
             ('5_1', '91'),
             ('6', '121'),
             ('7_0', '36'),
             ('7_1', '244'),
             ('8', '1'),
             ('9', '2'),
             ('10', '124'),
             ('11_1', '3'),
             ('12', '146'),
             ('13', '4'),
             ('14', '5'),
             ('15', '6'),
             ('16', '18'),
             ('17', '18'),
             ('18_0', '36'),
             ('18_1', '274'),
             ('19', '7'),
             ('20_0', '139'),
             ('20_1', '31'),
             ('20_2', '98'),
             ('21', '115'),
             ('22', '110_21'),
             ('23', '5'),
             ('24_0', '82'),
             ('24_1', '5'),
             ('25_1', '8'),
             ('26_0', '9'),
             ('26_1', '10'),
             ('26_2', '108'),
             ('27', '5'),
             ('29', '121'),


In [44]:
a

NameError: name 'a' is not defined

In [46]:
parseno=df_new_parsing['docno']
cluster=df_new_parsing['clusterNo']
myzip = zip(cluster,parseno)
clu_doc = dict(myzip)
len(clu_doc)

419

In [38]:
import natsort

In [39]:
natsort.natsorted(number.items())

[('2_0', '113'),
 ('2_1', '0'),
 ('3', '16'),
 ('4', '121'),
 ('5_0', '148'),
 ('5_1', '91'),
 ('6', '121'),
 ('7_0', '36'),
 ('7_1', '244'),
 ('8', '1'),
 ('9', '2'),
 ('10', '124'),
 ('11_1', '3'),
 ('12', '146'),
 ('13', '4'),
 ('14', '5'),
 ('15', '6'),
 ('16', '18'),
 ('17', '18'),
 ('18_0', '36'),
 ('18_1', '274'),
 ('19', '7'),
 ('20_0', '139'),
 ('20_1', '31'),
 ('20_2', '98'),
 ('21', '115'),
 ('22', '110_21'),
 ('23', '5'),
 ('24_0', '82'),
 ('24_1', '5'),
 ('25_1', '8'),
 ('26_0', '9'),
 ('26_1', '10'),
 ('26_2', '108'),
 ('27', '5'),
 ('29', '121'),
 ('30', '6'),
 ('31_0', '11'),
 ('31_1', '33'),
 ('32_0', '95'),
 ('32_1', '65'),
 ('33', '113'),
 ('34', '31'),
 ('35', '112'),
 ('36', '31'),
 ('37', '6'),
 ('38', '5'),
 ('39', '106'),
 ('40', '62_4'),
 ('41_0', '57'),
 ('41_1', '89'),
 ('42', '12'),
 ('43', '5'),
 ('44', '113'),
 ('45_0', '94_6'),
 ('45_1', '87'),
 ('45_2', '5'),
 ('46_1', '190'),
 ('46_2', '216'),
 ('46_3', '267'),
 ('47_1', '5'),
 ('48', '88'),
 ('49', '13

In [48]:
number

{'6980_1': '0',
 '8990': '0',
 '1606_2': '0',
 '10239': '0',
 '2514': '0',
 '1774': '0',
 '5684_5': '0',
 '124_2': '0',
 '8015': '0',
 '8360_1': '0',
 '6452': '0',
 '4776': '0',
 '5150': '0',
 '8019_0': '0',
 '1239_1': '0',
 '1024_1': '0',
 '7341': '0',
 '9318_2': '0',
 '3898_1': '0',
 '5586': '0',
 '3957_1': '0',
 '6919_1': '0',
 '3838_1': '0',
 '8040_2': '0',
 '4453': '0',
 '6857': '0',
 '818_1': '0',
 '4747_2': '0',
 '437_1': '0',
 '2195': '0',
 '2777_0': '0',
 '8734_2': '0',
 '7886_1': '0',
 '4167_3': '0',
 '9841_1': '0',
 '485_0': '0',
 '2_1': '0',
 '1566': '0',
 '7169_1': '0',
 '7896': '0',
 '8311_1': '0',
 '7865_1': '0',
 '2795': '0',
 '328': '0',
 '720_1': '0',
 '5384': '0',
 '6061_0': '0',
 '6384_1': '0',
 '6861': '0',
 '1886': '0',
 '2346': '0',
 '8183_0': '0',
 '7073_0': '0',
 '1580': '0',
 '7308': '0',
 '3289_1': '0',
 '489_1': '0',
 '6734_0': '1',
 '6402': '1',
 '9198_1': '1',
 '5449': '1',
 '10140_0': '1',
 '3484': '1',
 '9500': '1',
 '2790_0': '1',
 '1082_0': '1',
 '3026

In [47]:
result_doc

{'6980_1': '느낌이 좋다',
 '8990': '느낌이 좋다',
 '1606_2': '느낌이 좋다',
 '10239': '느낌이 좋다',
 '2514': '느낌이 좋다',
 '1774': '느낌이 좋다',
 '5684_5': '느낌이 좋다',
 '124_2': '느낌이 좋다',
 '8015': '느낌이 좋다',
 '8360_1': '느낌이 좋다',
 '6452': '느낌이 좋다',
 '4776': '느낌이 좋다',
 '5150': '느낌이 좋다',
 '8019_0': '느낌이 좋다',
 '1239_1': '느낌이 좋다',
 '1024_1': '느낌이 좋다',
 '7341': '느낌이 좋다',
 '9318_2': '느낌이 좋다',
 '3898_1': '느낌이 좋다',
 '5586': '느낌이 좋다',
 '3957_1': '느낌이 좋다',
 '6919_1': '느낌이 좋다',
 '3838_1': '느낌이 좋다',
 '8040_2': '느낌이 좋다',
 '4453': '느낌이 좋다',
 '6857': '느낌이 좋다',
 '818_1': '느낌이 좋다',
 '4747_2': '느낌이 좋다',
 '437_1': '느낌이 좋다',
 '2195': '느낌이 좋다',
 '2777_0': '느낌이 좋다',
 '8734_2': '느낌이 좋다',
 '7886_1': '느낌이 좋다',
 '4167_3': '느낌이 좋다',
 '9841_1': '느낌이 좋다',
 '485_0': '느낌이 좋다',
 '2_1': '느낌이 좋다',
 '1566': '느낌이 좋다',
 '7169_1': '느낌이 좋다',
 '7896': '느낌이 좋다',
 '8311_1': '느낌이 좋다',
 '7865_1': '느낌이 좋다',
 '2795': '느낌이 좋다',
 '328': '느낌이 좋다',
 '720_1': '느낌이 좋다',
 '5384': '느낌이 좋다',
 '6061_0': '느낌이 좋다',
 '6384_1': '느낌이 좋다',
 '6861': '느낌이 좋다',
 '1886': '느낌이 좋다'

# 마지막 결과파일

In [32]:
#input 데이터
path_raw = 'rawData.csv'

In [33]:
data = pd.read_csv(path_raw, names = None,encoding='cp949')
docno = data['no']
doc = data['응답값']

In [34]:
#{docno : doc}
myzip = zip(docno, doc)
raw_docs = dict(myzip)
len(raw_docs)

10400

In [34]:
raw_docs

{2: '씁쓸한 맛이 좋다. 톡쏘는 느낌이 좋다.',
 3: '시원함',
 4: '칼로리가 낮아서 많은 양을 먹어도 무리가 없음    맥주를 많이 마시는 편이기 때문에 배가 안 부른 맥주가 좋음',
 5: '칼로리 걱정을 조금 덜 할 수 있고 가볍게 마시기 참 좋다',
 6: '레몬맛이 좋아서',
 7: '내가 좋아하는 맛이다. 맥주의 고소한 맛과 탄산이 적절하게 들어가있다.',
 8: '가벼운맛',
 9: '맛이 깔끔함',
 10: '다른 맥주와 차별화 된 맛.',
 11: '브랜드 이미지, 즉 젊은 남자의 이미지를 가졌으며 맛또한 뛰어나다 특히 깔끔한 뒷맛이 좋다',
 12: '맥주거품맛이 부드럽다',
 13: '부드러워서',
 14: '맛있어요',
 15: '목넘김이 부드러워서',
 16: '맛이있어서',
 17: '톡쏘는 맛이 좋아서',
 18: '맛을 좋아해서 그 상표를 찾는다. 페트병맥주중에서는 선호 하는 맛이다.',
 19: '깔끔하다',
 20: '일반 생맥주나 캔맥주보다 맥주맛이 덜나고 순해서 마시기 편하다',
 21: '심플하다',
 22: '디자인이 이쁨',
 23: '맛있어서',
 24: '맛이 독특하고 맛있다',
 25: '흑맥주중에서도 저렴하고    맛이 덜씀',
 26: '거품이 부드럽고 목넘김이 좋다. 향또한 마찬가지',
 27: '맛있어서.  ',
 28: '쌉싸릅한 흑맥주  부드러운 거품  ',
 29: '레몬맛이 맛있음',
 30: '부드러운 목넘김',
 31: '맛이 부드럽고 끝맛이 좋음',
 32: '먹기 부담스럽지 않고 쉽게 먹을 수 있다',
 33: '시원한느낌이 좋아요.',
 34: '맛잇는 맥주라서 카스를 먹게된다.',
 35: '거품 엔젤링때문에',
 36: '맥주의 맛이 좋아서',
 37: '부드러운 목넘김때문에',
 38: '맛있어요',
 39: '선전에 공유가 나와서',
 40: '맛있기 때문에',
 41: '맥주가 부드럽고 쓴맛이 거의 없다',
 42: '똑쏘는 맛',
 43: '맛있다',
 44: '특유의

In [18]:
# final={}
# for key in raw_docs.keys():
#     coding=[]
#     for docno in result_doc.keys():
#         if str(key)==str(docno.split('_')[0]):
#             coding.append(result_doc[docno])
#     final[key]=coding

In [ ]:
# finallist=[]
# for key in raw_docs.keys():
#     row=[]
#     row.append(key)
#     row.append(raw_docs[key])
#     coding=[]
#     for docno in result_doc.keys():
#         if str(key)==str(docno.split('_')[0]):
#             coding.append(result_doc[docno])
#     row.extend(coding)   
#     finallist.append(row)

In [170]:
#Multi - coding title list로 결과만 뽑기
#[[docno, doc, clusterno1, title1, clusterno2, title2 ... ]]
finallist=[]
for key in raw_docs.keys():
    row=[]
    row.append(key)
    row.append(raw_docs[key])
    coding=[]
    for docno in number.keys():
        if str(key)==str(docno.split('_')[0]):
            coding.append(number[docno])
            coding.append(result_doc_cosine[docno])
#             coding.append(result_doc_euclidean[docno])
    row.extend(coding)   
    finallist.append(row)
    
with open('output1207_re.csv', 'w', newline='', encoding='CP949') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerows(finallist)

In [171]:
print(finallist)

[[2, '씁쓸한 맛이 좋다. 톡쏘는 느낌이 좋다.', '0', '느낌이 좋다', '113', '톡쏘는 맛이 일품이다'], [3, '시원함', '16', '시원하고'], [4, '칼로리가 낮아서 많은 양을 먹어도 무리가 없음    맥주를 많이 마시는 편이기 때문에 배가 안 부른 맥주가 좋음', '121', '레몬맛이 상쾌함을 줘서'], [5, '칼로리 걱정을 조금 덜 할 수 있고 가볍게 마시기 참 좋다', '148', '과일향에 간단히 부담없이 마실 수 있어서', '91', '친구들과 마시기 좋다'], [6, '레몬맛이 좋아서', '121', '레몬맛이 상쾌함을 줘서'], [7, '내가 좋아하는 맛이다. 맥주의 고소한 맛과 탄산이 적절하게 들어가있다.', '244', '마셔도 배가많이 안불러서 알콜도수가 낮아 순하다', '36', '맛이 내가좋아하는맛이다'], [8, '가벼운맛', '1', '가볍고'], [9, '맛이 깔끔함', '2', '맛이 깔끔하고'], [10, '다른 맥주와 차별화 된 맛.', '124', '가장 보편적으로 접할수 있고'], [11, '브랜드 이미지, 즉 젊은 남자의 이미지를 가졌으며 맛또한 뛰어나다 특히 깔끔한 뒷맛이 좋다', '3', '뒷맛이 깔끔하다'], [12, '맥주거품맛이 부드럽다', '146', '거품과 맛이 좋다'], [13, '부드러워서', '4', '부드럽고'], [14, '맛있어요', '5', '맛있다'], [15, '목넘김이 부드러워서', '6', '목넘김이 부드럽고'], [16, '맛이있어서', '18', '맛이 순함'], [17, '톡쏘는 맛이 좋아서', '18', '맛이 순함'], [18, '맛을 좋아해서 그 상표를 찾는다. 페트병맥주중에서는 선호 하는 맛이다.', '274', '최근 맥주중에 가장 깔끔한 맛이 나서 선호합니다', '36', '맛이 내가좋아하는맛이다'], [19, '깔끔하다', '7', '깔끔하고'], [20, '일반 생맥주나 캔맥주보다 맥주맛이 덜나고 순해서 마시기 편하다', '139', '캔

# Raw&Parsing Entropy

In [47]:
parsingdict={}
for key in raw_docs.keys():
    coding=[]
    for docno in number.keys():
        if str(key)==str(docno.split('_')[0]):
            coding.append(number[docno])
    natsort.natsorted(coding)        
    parsingdict[key]=coding

In [48]:
# {docno : [clusterno]}
parsingdict

{2: ['113', '0'],
 3: ['16'],
 4: ['121'],
 5: ['148', '91'],
 6: ['121'],
 7: ['36', '244'],
 8: ['1'],
 9: ['2'],
 10: ['124'],
 11: ['3'],
 12: ['146'],
 13: ['4'],
 14: ['5'],
 15: ['6'],
 16: ['18'],
 17: ['18'],
 18: ['36', '274'],
 19: ['7'],
 20: ['139', '31', '98'],
 21: ['115'],
 22: ['110_21'],
 23: ['5'],
 24: ['82', '5'],
 25: ['8'],
 26: ['9', '10', '108'],
 27: ['5'],
 28: [],
 29: ['121'],
 30: ['6'],
 31: ['11', '33'],
 32: ['95', '65'],
 33: ['113'],
 34: ['31'],
 35: ['112'],
 36: ['31'],
 37: ['6'],
 38: ['5'],
 39: ['106'],
 40: ['62_4'],
 41: ['57', '89'],
 42: ['12'],
 43: ['5'],
 44: ['113'],
 45: ['94_6', '87', '5'],
 46: ['190', '216', '267'],
 47: ['5'],
 48: ['88'],
 49: ['13'],
 50: [],
 51: ['2', '14'],
 52: ['15'],
 53: ['6', '2'],
 54: ['110_1', '16', '45', '106'],
 55: ['11'],
 56: ['94_1'],
 57: ['209', '83'],
 58: ['115'],
 59: ['6', '2'],
 60: ['2'],
 61: ['229'],
 62: ['46', '110_13'],
 63: ['212', '98'],
 64: ['16', '178'],
 65: ['12', '134', '139'

In [49]:
# {clusterno : [docno]} parsing data
parse_docno_cluster

{'0': ['6980_1',
  '8990',
  '1606_2',
  '10239',
  '2514',
  '1774',
  '5684_5',
  '124_2',
  '8015',
  '8360_1',
  '6452',
  '4776',
  '5150',
  '8019_0',
  '1239_1',
  '1024_1',
  '7341',
  '9318_2',
  '3898_1',
  '5586',
  '3957_1',
  '6919_1',
  '3838_1',
  '8040_2',
  '4453',
  '6857',
  '818_1',
  '4747_2',
  '437_1',
  '2195',
  '2777_0',
  '8734_2',
  '7886_1',
  '4167_3',
  '9841_1',
  '485_0',
  '2_1',
  '1566',
  '7169_1',
  '7896',
  '8311_1',
  '7865_1',
  '2795',
  '328',
  '720_1',
  '5384',
  '6061_0',
  '6384_1',
  '6861',
  '1886',
  '2346',
  '8183_0',
  '7073_0',
  '1580',
  '7308',
  '3289_1',
  '489_1'],
 '1': ['6734_0',
  '6402',
  '9198_1',
  '5449',
  '10140_0',
  '3484',
  '9500',
  '2790_0',
  '1082_0',
  '3026_1',
  '5749_1',
  '7280_0',
  '5542',
  '6356',
  '4726_0',
  '1883_1',
  '6662_2',
  '7981_0',
  '5142_0',
  '3930_0',
  '6386_0',
  '2908',
  '6975_0',
  '4771',
  '1410_2',
  '5048_1',
  '1168',
  '8042_1',
  '8073_1',
  '1517_1',
  '4846_1',
  '11

In [81]:
# {cluster:[docno]} rawdata
docno_cluster

{'0': [8828,
  2951,
  8632,
  8448,
  10013,
  5086,
  9394,
  8762,
  5763,
  7968,
  908,
  297,
  1554,
  5961,
  3432,
  7292,
  2549,
  7396,
  1014,
  5772,
  8129,
  4148,
  7057,
  4203,
  3651,
  6459,
  6809,
  2446,
  9155,
  4528,
  6088,
  6316,
  4564,
  3333,
  10344,
  8856,
  9480,
  6619,
  4042,
  8584,
  9567,
  3351,
  6368,
  8203,
  9274,
  2526,
  2724,
  4745,
  2465,
  9027,
  3977,
  8379,
  1954,
  8663,
  6220,
  6203,
  9195,
  1898,
  3608,
  4328,
  10076,
  9526,
  794,
  2159,
  3360,
  5012,
  4060,
  64,
  8392,
  8105,
  809,
  4673,
  5549,
  4684,
  9748,
  2477,
  8941,
  7083,
  7676,
  3755,
  3637,
  5386,
  4460,
  4761,
  7867,
  8844,
  10188,
  8596,
  3476,
  1777,
  2551,
  4044,
  2779,
  2867,
  9012,
  4524,
  753,
  1205,
  7080,
  8771,
  4724,
  3469,
  5674,
  3958,
  3255,
  10216,
  9928,
  9729,
  9602,
  2913,
  1808,
  3972,
  3908,
  8340,
  1701,
  775,
  4652,
  3,
  3038,
  8327,
  1959,
  6899,
  5925,
  1081,
  7659,
 

In [50]:
# Entropy 계산
# {rawclusterno : [[parsing_clusterno, count]]}
pair_dic={}
for rawclno in docno_cluster.keys():
    li = []
    for docno in docno_cluster[rawclno]:
        if parsingdict[docno] !=[]:
            li.append(parsingdict[docno][0])
    
    unique, counts = np.unique(li, return_counts=True)
    k=np.stack((unique,counts),axis=1).tolist()
    
    pair_dic[rawclno]=k

In [51]:
pair_dic

{'0': [['103', '1'],
  ['105', '1'],
  ['12', '1'],
  ['13', '2'],
  ['16', '96'],
  ['170', '1'],
  ['18', '2'],
  ['20', '45'],
  ['27', '1'],
  ['39', '1'],
  ['62_5', '1'],
  ['78', '2'],
  ['79', '3']],
 '1': [['110_1', '1'],
  ['110_13', '1'],
  ['112', '1'],
  ['12', '2'],
  ['13', '2'],
  ['158', '1'],
  ['18', '2'],
  ['2', '207'],
  ['33', '10'],
  ['39', '4'],
  ['48', '4'],
  ['62_5', '1'],
  ['7', '131'],
  ['8', '2'],
  ['94_2', '1']],
 '10': [['108', '1'],
  ['12', '2'],
  ['13', '2'],
  ['18', '1'],
  ['310', '1'],
  ['41', '2'],
  ['55', '15'],
  ['60', '22'],
  ['66_3', '1']],
 '100': [['111', '1'],
  ['135', '1'],
  ['143', '4'],
  ['170', '1'],
  ['177', '1'],
  ['18', '1'],
  ['217', '1'],
  ['229', '2'],
  ['43', '1'],
  ['49', '1']],
 '101': [['113', '7'],
  ['118', '1'],
  ['200', '1'],
  ['212', '1'],
  ['4', '1'],
  ['63', '1'],
  ['88', '1']],
 '102': [['109', '1'],
  ['118', '20'],
  ['128', '1'],
  ['129', '1'],
  ['134', '5'],
  ['154', '2'],
  ['155', '1'

In [52]:
# calculate_entropy
entropy_list=[]
for i in pair_dic.keys():
    entropy=0
    for j in range(len(pair_dic[i])):
        p_i=(int(pair_dic[i][j][1])/len(docno_cluster[i]))
        entropy += p_i * math.log(1/p_i)
    entropy_list.append([i, entropy])

In [53]:
entropy_list

[['0', 1.1250691910606019],
 ['1', 1.09597585109799],
 ['10', 1.4216502236269417],
 ['100', 1.9927981441098428],
 ['101', 1.4775981601150834],
 ['102', 1.9843357813663975],
 ['103', 2.2391031010518803],
 ['104', 1.7716239556773663],
 ['105', 1.6690961427718418],
 ['106', 2.166084939249829],
 ['107', 1.9554481056713506],
 ['108', 2.441015278026703],
 ['109', 2.224474643159943],
 ['11', 1.379560226115235],
 ['110', 2.5275135210287294],
 ['111', 1.234267866079077],
 ['112', 1.4105135571148382],
 ['113', 1.158185740427404],
 ['114', 0.6844611803701096],
 ['115', 2.2610075329552735],
 ['116', 1.3345506928718538],
 ['117', 1.2846318812158009],
 ['118', 1.5171515848932915],
 ['119', 2.245035274126178],
 ['12', 0.783253478241602],
 ['120', 2.5649493574615376],
 ['121', 2.053878033351256],
 ['122', 1.8663999394996524],
 ['123', 2.0982737395252498],
 ['124', 1.4508050200839238],
 ['125', 1.7677614722893296],
 ['126', 1.9336971475826519],
 ['127', 1.5868844169650473],
 ['128', 2.277831095639001],

In [79]:
# Entorpy 기준 : 2.75
clu_entro=np.array(entropy_list)
select_entropy = clu_entro[clu_entro[:,1].astype(np.float)>2.75]
print(select_entropy)
select_cluster=slect_entropy[:,0]
print(select_cluster)

[['129' '2.902002313205604']
 ['135' '2.7888535522534674']
 ['25' '2.755859410872371']
 ['30' '3.0030009545928777']
 ['31' '3.2799855518798675']
 ['33' '2.938654129343915']
 ['34' '3.026798975069659']
 ['35' '2.810093545464983']
 ['36' '3.500568301227595']
 ['38' '2.800332718207882']
 ['44' '3.1091427859613128']
 ['47' '2.9959122558987303']
 ['55' '3.089368978056943']
 ['57' '3.036906448553584']
 ['58' '3.304986279080028']
 ['63' '2.8246199448266642']
 ['67' '2.7725887222397807']
 ['89' '3.1998536630896113']]
['129' '135' '25' '30' '31' '33' '34' '35' '36' '38' '44' '47' '55' '57'
 '58' '63' '67' '89']


In [78]:
select_cluster=slect_entropy[:,0]

# Token 비교

In [75]:
data = pd.read_csv('codedata/token/tokenTM_raw.csv', names = None,encoding='cp949')
raw_docno=data['KEY']
raw_token =[doc.split(' ') for doc in data['raw_doc_tu']]

In [76]:
myzip = zip(raw_docno, raw_token)
raw_docno_token = dict(myzip)
len(raw_docno_token)

10205

In [80]:
raw_docno_token

{2: ['씁쓸', '맛', '느낌'],
 3: ['시원'],
 4: ['칼로리', '양', '무리', '맥주', '마시', '편', '때문', '배', '부르', '맥주'],
 5: ['칼로리', '걱정', '수', '가볍', '마시'],
 6: ['레몬', '맛'],
 7: ['내', '좋아하', '맛', '맥주', '고소', '맛', '탄산', '적절', '들어가'],
 8: ['가볍', '맛'],
 9: ['맛', '깔끔'],
 10: ['맥주', '차별', '맛'],
 11: ['브랜드', '이미지', '젊은', '남자', '이미지', '가지', '맛', '뛰어나', '깔끔', '뒷맛'],
 12: ['맥주', '거품', '맛', '부드럽'],
 13: ['부드럽'],
 14: ['맛있'],
 15: ['목', '넘기', '부드럽'],
 16: ['맛'],
 17: ['맛'],
 18: ['맛', '좋아하', '상표', '페트병', '맥주', '중', '선호', '맛'],
 19: ['깔끔'],
 20: ['일반', '맥주', '캔', '맥주', '맥주', '맛', '순', '마시', '편하'],
 21: ['심플'],
 22: ['디자인', '이쁘'],
 23: ['맛있'],
 24: ['맛', '독특', '맛있'],
 25: ['흑', '맥주', '중', '저렴', '맛'],
 26: ['거품', '부드럽', '목', '넘기', '향', '마찬가지'],
 27: ['맛있'],
 28: ['흑', '맥주', '부드럽', '거품'],
 29: ['레몬', '맛', '맛있'],
 30: ['부드럽', '목', '넘기'],
 31: ['맛', '부드럽', '끝', '맛'],
 32: ['부담', '수'],
 33: ['시원', '느낌'],
 34: ['맛', '맥주', '카스'],
 35: ['거품', '엔젤', '링', '때문'],
 36: ['맥주', '맛'],
 37: ['부드럽', '목', '넘기', '때문'],
 38: ['맛있'],
 39: [

In [81]:
data2 = pd.read_csv('codedata/token/tokenTM_parsed.csv', names = None,encoding='cp949')
parse_docno=data2['KEY']
parse_token =[doc.split(' ') for doc in data2['raw_doc_tu']]

In [82]:
parse_token

[['씁쓸', '맛'],
 ['느낌'],
 ['시원'],
 ['칼로리', '양', '무리', '맥주', '마시', '편', '때문', '배', '부르', '맥주'],
 ['칼로리', '걱정', '수'],
 ['가볍', '마시'],
 ['레몬', '맛'],
 ['내', '좋아하', '맛'],
 ['맥주', '고소', '맛', '탄산', '적절', '들어가'],
 ['가볍', '맛'],
 ['맛', '깔끔'],
 ['맥주', '차별', '맛'],
 ['브랜드', '이미지', '젊은', '남자', '이미지', '가지', '맛', '뛰어나'],
 ['깔끔', '뒷맛'],
 ['맥주', '거품', '맛', '부드럽'],
 ['부드럽'],
 ['맛있'],
 ['목', '넘기', '부드럽'],
 ['맛'],
 ['맛'],
 ['맛', '좋아하', '상표'],
 ['페트병', '맥주', '중', '선호', '맛'],
 ['깔끔'],
 ['일반', '맥주', '캔', '맥주'],
 ['맥주', '맛'],
 ['순', '마시', '편하'],
 ['심플'],
 ['디자인', '이쁘'],
 ['맛있'],
 ['맛', '독특'],
 ['맛있'],
 ['흑', '맥주', '중', '저렴'],
 ['맛'],
 ['거품', '부드럽'],
 ['목', '넘기'],
 ['향', '마찬가지'],
 ['맛있'],
 ['흑', '맥주', '부드럽', '거품'],
 ['레몬', '맛', '맛있'],
 ['부드럽', '목', '넘기'],
 ['맛', '부드럽'],
 ['끝', '맛'],
 ['부담'],
 ['수'],
 ['시원', '느낌이', '좋아'],
 ['맛', '맥주', '카스'],
 ['거품', '엔젤', '링', '때문'],
 ['맥주', '맛'],
 ['부드럽', '목', '넘기', '때문'],
 ['맛있'],
 ['선전', '공유', '나오'],
 ['맛있', '때문'],
 ['맥주', '부드럽'],
 ['쓴맛'],
 ['맛'],
 ['맛있'],
 ['특유', '향', '맛', '일품'

In [83]:
myzip = zip(parse_docno, parse_token)
parse_docno_token = dict(myzip)
len(parse_docno_token)

15527

In [84]:
parse_docno_token

{'2_0': ['씁쓸', '맛'],
 '2_1': ['느낌'],
 '3': ['시원'],
 '4': ['칼로리', '양', '무리', '맥주', '마시', '편', '때문', '배', '부르', '맥주'],
 '5_0': ['칼로리', '걱정', '수'],
 '5_1': ['가볍', '마시'],
 '6': ['레몬', '맛'],
 '7_0': ['내', '좋아하', '맛'],
 '7_1': ['맥주', '고소', '맛', '탄산', '적절', '들어가'],
 '8': ['가볍', '맛'],
 '9': ['맛', '깔끔'],
 '10': ['맥주', '차별', '맛'],
 '11_0': ['브랜드', '이미지', '젊은', '남자', '이미지', '가지', '맛', '뛰어나'],
 '11_1': ['깔끔', '뒷맛'],
 '12': ['맥주', '거품', '맛', '부드럽'],
 '13': ['부드럽'],
 '14': ['맛있'],
 '15': ['목', '넘기', '부드럽'],
 '16': ['맛'],
 '17': ['맛'],
 '18_0': ['맛', '좋아하', '상표'],
 '18_1': ['페트병', '맥주', '중', '선호', '맛'],
 '19': ['깔끔'],
 '20_0': ['일반', '맥주', '캔', '맥주'],
 '20_1': ['맥주', '맛'],
 '20_2': ['순', '마시', '편하'],
 '21': ['심플'],
 '22': ['디자인', '이쁘'],
 '23': ['맛있'],
 '24_0': ['맛', '독특'],
 '24_1': ['맛있'],
 '25_0': ['흑', '맥주', '중', '저렴'],
 '25_1': ['맛'],
 '26_0': ['거품', '부드럽'],
 '26_1': ['목', '넘기'],
 '26_2': ['향', '마찬가지'],
 '27': ['맛있'],
 '28': ['흑', '맥주', '부드럽', '거품'],
 '29': ['레몬', '맛', '맛있'],
 '30': ['부드럽', '목', '

In [ ]:
##############rawdata!
# # {cluster:[docno]} rawdata
# docno_cluster

#     #{clusterno : title}
# title_raw_eucli[c]=cluster_doc_rawdata[c][np.argmin(eucli)]
# title_raw_cosine[c]=cluster_doc_rawdata[c][np.argmin(cosine)]

# #{clusterno : title num}
# num_title_raw_eucli[c]=docno_cluster[c][np.argmin(eucli)]
# num_title_raw_cosine[c]=docno_cluster[c][np.argmin(cosine)]


##########parsing data!
# # {rawdocno : [clusterno]} parsing data
# parsingdict
# # {clusterno : [docno]} parsing data
# parse_docno_cluster


# #{clusterno : title}
# parse_title_raw_eucli[c]=parse_cluster_doc_rawdata[c][np.argmin(eucli)]
# parse_title_raw_cosine[c]=parse_cluster_doc_rawdata[c][np.argmin(cosine)]

# #{clusterno : title docno}
# parse_num_title_raw_eucli[c]=parse_docno_cluster[c][np.argmin(eucli)]
# parse_num_title_raw_cosine[c]=parse_docno_cluster[c][np.argmin(cosine)]


In [85]:
len(parsingdict)

10400

In [86]:
parse_docno_cluster

{'0': ['6980_1',
  '8990',
  '1606_2',
  '10239',
  '2514',
  '1774',
  '5684_5',
  '124_2',
  '8015',
  '8360_1',
  '6452',
  '4776',
  '5150',
  '8019_0',
  '1239_1',
  '1024_1',
  '7341',
  '9318_2',
  '3898_1',
  '5586',
  '3957_1',
  '6919_1',
  '3838_1',
  '8040_2',
  '4453',
  '6857',
  '818_1',
  '4747_2',
  '437_1',
  '2195',
  '2777_0',
  '8734_2',
  '7886_1',
  '4167_3',
  '9841_1',
  '485_0',
  '2_1',
  '1566',
  '7169_1',
  '7896',
  '8311_1',
  '7865_1',
  '2795',
  '328',
  '720_1',
  '5384',
  '6061_0',
  '6384_1',
  '6861',
  '1886',
  '2346',
  '8183_0',
  '7073_0',
  '1580',
  '7308',
  '3289_1',
  '489_1'],
 '1': ['6734_0',
  '6402',
  '9198_1',
  '5449',
  '10140_0',
  '3484',
  '9500',
  '2790_0',
  '1082_0',
  '3026_1',
  '5749_1',
  '7280_0',
  '5542',
  '6356',
  '4726_0',
  '1883_1',
  '6662_2',
  '7981_0',
  '5142_0',
  '3930_0',
  '6386_0',
  '2908',
  '6975_0',
  '4771',
  '1410_2',
  '5048_1',
  '1168',
  '8042_1',
  '8073_1',
  '1517_1',
  '4846_1',
  '11

In [87]:
parsingdict

{2: ['113', '0'],
 3: ['16'],
 4: ['121'],
 5: ['148', '91'],
 6: ['121'],
 7: ['36', '244'],
 8: ['1'],
 9: ['2'],
 10: ['124'],
 11: ['3'],
 12: ['146'],
 13: ['4'],
 14: ['5'],
 15: ['6'],
 16: ['18'],
 17: ['18'],
 18: ['36', '274'],
 19: ['7'],
 20: ['139', '31', '98'],
 21: ['115'],
 22: ['110_21'],
 23: ['5'],
 24: ['82', '5'],
 25: ['8'],
 26: ['9', '10', '108'],
 27: ['5'],
 28: [],
 29: ['121'],
 30: ['6'],
 31: ['11', '33'],
 32: ['95', '65'],
 33: ['113'],
 34: ['31'],
 35: ['112'],
 36: ['31'],
 37: ['6'],
 38: ['5'],
 39: ['106'],
 40: ['62_4'],
 41: ['57', '89'],
 42: ['12'],
 43: ['5'],
 44: ['113'],
 45: ['94_6', '87', '5'],
 46: ['190', '216', '267'],
 47: ['5'],
 48: ['88'],
 49: ['13'],
 50: [],
 51: ['2', '14'],
 52: ['15'],
 53: ['6', '2'],
 54: ['110_1', '16', '45', '106'],
 55: ['11'],
 56: ['94_1'],
 57: ['209', '83'],
 58: ['115'],
 59: ['6', '2'],
 60: ['2'],
 61: ['229'],
 62: ['46', '110_13'],
 63: ['212', '98'],
 64: ['16', '178'],
 65: ['12', '134', '139'

In [88]:
docno_cluster

{'0': [8828,
  2951,
  8632,
  8448,
  10013,
  5086,
  9394,
  8762,
  5763,
  7968,
  908,
  297,
  1554,
  5961,
  3432,
  7292,
  2549,
  7396,
  1014,
  5772,
  8129,
  4148,
  7057,
  4203,
  3651,
  6459,
  6809,
  2446,
  9155,
  4528,
  6088,
  6316,
  4564,
  3333,
  10344,
  8856,
  9480,
  6619,
  4042,
  8584,
  9567,
  3351,
  6368,
  8203,
  9274,
  2526,
  2724,
  4745,
  2465,
  9027,
  3977,
  8379,
  1954,
  8663,
  6220,
  6203,
  9195,
  1898,
  3608,
  4328,
  10076,
  9526,
  794,
  2159,
  3360,
  5012,
  4060,
  64,
  8392,
  8105,
  809,
  4673,
  5549,
  4684,
  9748,
  2477,
  8941,
  7083,
  7676,
  3755,
  3637,
  5386,
  4460,
  4761,
  7867,
  8844,
  10188,
  8596,
  3476,
  1777,
  2551,
  4044,
  2779,
  2867,
  9012,
  4524,
  753,
  1205,
  7080,
  8771,
  4724,
  3469,
  5674,
  3958,
  3255,
  10216,
  9928,
  9729,
  9602,
  2913,
  1808,
  3972,
  3908,
  8340,
  1701,
  775,
  4652,
  3,
  3038,
  8327,
  1959,
  6899,
  5925,
  1081,
  7659,
 

In [90]:
# #{clusternum(raw기준):[[docno(raw기준), selection]]}
# result={}
# for clusterno in docno_cluster.keys(): #모든 cluster에 대해서
# # for clusterno in docno_cluster.keys(): #Entropy 기준에 해당하는 cluster에 대해서
#     raw_titleno = num_title_raw_cosine[clusterno]
#     raw_title_token = raw_docno_token[raw_titleno] # title token
#     result_docno_titleselect=[]
    
#     for docno in docno_cluster[clusterno]:
#         rawdoc_token=raw_docno_token[docno] # rawdoc token
#         parse_clusternum=parsingdict[docno] 
#         all_parse_title_token=[]
#         docno_titleselect=[]
#         print(docno)
#         parse_select_result=[]
#         for parse_clno in parse_clusternum:
#             parse_titleno=parse_num_title_raw_cosine[parse_clno]
#             all_parse_title_token.extend(parse_docno_token[parse_titleno]) #각 doc별 다중코딩 총 title token
#             parse_select_result.append(parse_clno)
#             parse_select_result.append(parse_title_raw_cosine[parse_clno])
            
#         raw_matchcount=0
#         parse_matchcount=0
#         print(list(set(rawdoc_token)))
#         print(list(set(raw_title_token)))
#         print(list(set(all_parse_title_token)))
#         for i in list(set(rawdoc_token)):
#             raw_matchcount+=list(set(raw_title_token)).count(i)
#             parse_matchcount+=list(set(all_parse_title_token)).count(i)
        
#         print(raw_matchcount,parse_matchcount)
#         docno_titleselect.append(docno)
        
#         #분수형태:
#         if len(raw_title_token) != 0:
#             raw_matchscore = raw_matchcount/len(raw_title_token)
#         else:
#             raw_matchscore=0
#         if len(all_parse_title_token) != 0:
#             parse_matchscore = parse_matchcount/len(all_parse_title_token)
#         else:
#             parse_matchscore=0
        
#         print(raw_matchscore,parse_matchscore)
        
# #         if raw_matchcount >= parse_matchcount :
#         if raw_matchscore >= parse_matchscore :
#             selection=0 #raw title선택
#             docno_titleselect.append(selection)
#             docno_titleselect.append(title_raw_cosine[clusterno])
#         else : 
#             selection=1 #parsing title선택
#             docno_titleselect.append(selection)
#             docno_titleselect.extend(parse_select_result)
        

        
#         result_docno_titleselect.append(docno_titleselect)
    
#     result[clusterno] = result_docno_titleselect
    

8828
['시원']
['시원']
['시원']
1 1
1.0 1.0
2951
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
8632
['시원']
['시원']
['시원']
1 1
1.0 1.0
8448
['맛', '것', '시원']
['시원']
['것', '풍부', '맛', '시원']
1 3
1.0 0.6
10013
['때', '맛', '것', '병', '소리', '시원', '딸']
['시원']
['때', '반하', '맛', '것', '일본', '맥주', '풍부']
1 3
1.0 0.42857142857142855
5086
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
9394
['시원']
['시원']
['시원']
1 1
1.0 1.0
8762
['시원']
['시원']
['시원']
1 1
1.0 1.0
5763
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
7968
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
908
['시원']
['시원']
['시원']
1 1
1.0 1.0
297
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
1554
['시원']
['시원']
['시원']
1 1
1.0 1.0
5961
['시원', '금']
['시원']
['시원']
1 1
1.0 1.0
3432
['시원']
['시원']
['시원']
1 1
1.0 1.0
7292
['시원']
['시원']
['시원']
1 1
1.0 1.0
2549
['합', '시원']
['시원']
['시원']
1 1
1.0 1.0
7396
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
1014
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
5772
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1.0
8129
['맛', '시원']
['시원']
['맛', '시원']
1 2
1.0 1

['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
1027
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
6931
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
10283
['깔끔', '입', '맛']
['깔끔', '맛']
['깔끔', '입']
2 2
1.0 1.0
8247
['깔끔']
['깔끔', '맛']
['깔끔']
1 1
0.5 1.0
5543
['깔끔', '시다', '맛', '체고']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
5445
['깔끔']
['깔끔', '맛']
['깔끔']
1 1
0.5 1.0
9052
['깔끔']
['깔끔', '맛']
['깔끔']
1 1
0.5 1.0
5995
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
7794
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
4870
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
5475
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
507
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
3401
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
9976
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
7964
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
2713
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
871
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛', '순함']
2 2
1.0 0.6666666666666666
6650
['깔끔', '맛']
['깔끔', '맛']
['깔끔', '맛']
2 2
1.0 1.0
890

['맛', '일품']
2 0
1.0 0.0
3073
['맛', '넘기', '맥주', '시원', '느낌이', '목', '좋아']
['느낌이', '좋아']
['넘기', '시원', '느낌이', '목', '좋아']
2 5
1.0 1.0
2692
['느낌이', '좋아']
['느낌이', '좋아']
['맛', '일품']
2 0
1.0 0.0
2788
['때', '마실', '느낌이', '느낌', '부드럽', '좋아', '강하']
['느낌이', '좋아']
['목', '마실', '때', '넘기']
2 2
1.0 0.5
945
['느낌이', '좋아']
['느낌이', '좋아']
['맛', '일품']
2 0
1.0 0.0
4346
['들어가', '보리', '느낌', '꺼']
['느낌이', '좋아']
[]
0 0
0.0 0
4391
['과일', '들어가', '맛있', '맛나']
['느낌이', '좋아']
['상쾌', '달콤', '맛', '레몬']
0 0
0.0 0.0
3045
['나서', '맛', '맛있', '음료수']
['달콤', '맛']
['맛', '나서', '부드럽', '옥수수', '향']
1 2
0.5 0.4
7804
['맥주', '맛', '다양']
['달콤', '맛']
['맛', '다양']
1 2
0.5 1.0
8611
['달콤', '맛']
['달콤', '맛']
['달콤', '맛']
2 2
1.0 1.0
2669
['비교', '맛', '흑', '맥주', '풍부', '향']
['달콤', '맛']
['향', '맛']
1 2
0.5 1.0
3662
['과일', '나서', '맛', '맛있']
['달콤', '맛']
['달콤', '맛']
1 1
0.5 0.5
6596
['맛', '다양']
['달콤', '맛']
['맛', '다양']
1 2
0.5 1.0
5688
['과일', '향', '적절', '도수']
['달콤', '맛']
['향', '수', '구하']
0 1
0.0 0.3333333333333333
7615
['달콤', '맛']
['달콤', '맛']
['달콤', '맛']
2 2
1.0 

9303
['맘', '카스', '맥주', '남자', '카피']
['맥주', '어우러지', '디자인', '상표', '색']
[]
1 0
0.2 0
3804
['맛', '맥주', '어우러지', '과즙', '때문']
['맥주', '어우러지', '디자인', '상표', '색']
['산토리', '맥주', '맛있']
2 1
0.4 0.3333333333333333
4128
['대하', '거품', '맛있', '이야기']
['맥주', '어우러지', '디자인', '상표', '색']
['대하', '호감', '김연아']
0 1
0.0 0.3333333333333333
4373
['탄산', '맛', '맥주', '어우러지', '시원', '거', '나']
['맥주', '어우러지', '디자인', '상표', '색']
['산토리', '맥주', '맛있']
2 1
0.4 0.3333333333333333
584
['맥주', '어우러지', '디자인', '상표', '색']
['맥주', '어우러지', '디자인', '상표', '색']
['산토리', '맥주', '맛있']
5 1
1.0 0.3333333333333333
7558
['씁쓸', '맛', '것', '넘기', '특유', '맥주', '거품', '어우러지', '부드럽', '목', '적당']
['맥주', '어우러지', '디자인', '상표', '색']
['보리', '맛', '넘기', '맥주', '부드럽', '목', '강하', '다르']
2 5
0.4 0.625
6362
['맛', '맥주', '어우러지', '마시', '깔끔', '수', '레몬']
['맥주', '어우러지', '디자인', '상표', '색']
['산토리', '맥주', '맛있']
2 1
0.4 0.3333333333333333
5873
['눈', '마시', '맥주', '초기', '독특', '카피']
['맥주', '어우러지', '디자인', '상표', '색']
['느끼', '청량감', '마시']
1 1
0.2 0.3333333333333333
9014
['진정', '내용', '예전', '친구', '

['말아먹', '맛있', '소맥']
['맛', '때문', '소맥']
3 1
1.0 0.3333333333333333
8000
['타', '소맥']
['말아먹', '맛있', '소맥']
['맛', '때문', '소맥']
1 1
0.3333333333333333 0.3333333333333333
6964
['일반', '때', '소맥', '카스', '마실', '느낌', '음']
['말아먹', '맛있', '소맥']
['때', '이름', '마실', '넘기', '시원', '느낌', '자체', '목']
1 3
0.3333333333333333 0.375
9735
['뒷맛', '맥주', '맛', '소맥']
['말아먹', '맛있', '소맥']
['맛', '맥주', '남자']
1 2
0.3333333333333333 0.6666666666666666
6883
['좋아하', '맛있', '소맥']
['말아먹', '맛있', '소맥']
[]
2 0
0.6666666666666666 0
3594
['때', '맛', '소맥', '넘기', '마실', '상쾌', '목']
['말아먹', '맛있', '소맥']
['때', '넘기', '마실', '시원', '목']
1 4
0.3333333333333333 0.5714285714285714
3912
['때', '맛있', '소맥']
['말아먹', '맛있', '소맥']
['때', '맥주', '반하', '일본']
2 1
0.6666666666666666 0.25
9688
['부드럽', '넘어가', '맛', '소맥']
['말아먹', '맛있', '소맥']
['독특', '맛', '부드럽']
1 2
0.3333333333333333 0.6666666666666666
9322
['맛', '친구', '추천', '시원']
['맛', '친구', '추천', '시원']
['맛', '친구', '추천', '시원']
4 4
1.0 1.0
1133
['때', '맛', '마실', '맥주', '중요', '느낌', '깔끔']
['맛', '친구', '추천', '시원']
['목', '마실', 

...

['맛', '거품', '풍부', '부드럽']
['맛', '거품', '맥주', '남자', '부드럽']
4 4
1.0 0.8
6606
['맛', '맛있', '풍부', '내', '느낌', '부드럽', '잡']
['맛', '거품', '풍부', '부드럽']
['맛', '입맛', '맛있', '깨끗', '풍부', '내', '느낌']
3 5
0.75 0.7142857142857143
9853
['넘기', '거품', '맥주', '풍부', '부드럽', '목']
['맛', '거품', '풍부', '부드럽']
['맛', '넘기', '맥주', '부드럽', '목', '향']
3 4
0.75 0.6666666666666666
5293
['거품', '풍부', '맛', '부드럽']
['맛', '거품', '풍부', '부드럽']
['맛', '거품', '풍부', '때문', '부드럽', '향']
4 4
1.0 0.5714285714285714
1484
['맛', '거품', '흑', '맥주', '부드럽']
['맛', '거품', '풍부', '부드럽']
[]
3 0
0.75 0
2695
['거품', '풍부', '부드럽']
['맛', '거품', '풍부', '부드럽']
['맛', '거품', '때문', '부드럽', '향']
3 2
0.75 0.4
4994
['맛', '거품', '풍부', '부드럽']
['맛', '거품', '풍부', '부드럽']
['맛', '거품', '때문', '부드럽', '향']
4 3
1.0 0.6
1173
['거품', '맥주', '부드럽']
['맛', '거품', '풍부', '부드럽']
['거품', '맛']
2 1
0.5 0.5
8914
['신선']
['신선']
['느낌', '신선']
1 1
1.0 0.5
616
['신선']
['신선']
['느낌', '신선']
1 1
1.0 0.5
3878
['이름']
['신선']
['이름']
0 1
0.0 1.0
3355
['신선']
['신선']
['느낌', '신선']
1 1
1.0 0.5
7170
['느낌', '자체', '이름', '색', '예쁘']
['

9149
['목', '거품', '삼키', '부드럽']
['맛', '맛있', '거품', '부드럽', '깔끔']
['거품', '부드럽']
2 2
0.4 1.0
6912
['넘기', '거품', '풍부', '부드럽', '목']
['맛', '맛있', '거품', '부드럽', '깔끔']
['거품', '풍부', '때문', '부드럽']
2 3
0.4 0.75
1445
['목', '넘기', '거품', '부드럽']
['맛', '맛있', '거품', '부드럽', '깔끔']
['목', '넘기', '부드럽']
2 3
0.4 1.0
855
['거품', '마시', '나서', '뒷맛', '부드럽']
['맛', '맛있', '거품', '부드럽', '깔끔']
['맛', '거품', '나서', '때문', '부드럽', '진한', '향']
2 3
0.4 0.375
10382
['넘기', '거품', '부드럽', '목', '일품']
['맛', '맛있', '거품', '부드럽', '깔끔']
['넘기', '거품', '시원', '부드럽', '목']
2 4
0.4 0.8
8707
['맛있', '거품', '맥주', '달콤', '부드럽']
['맛', '맛있', '거품', '부드럽', '깔끔']
['맛', '거품', '때문', '부드럽', '향']
3 2
0.6 0.4
3534
['넘', '거품', '갈증', '해소', '느낌', '김', '부드럽', '목']
['맛', '맛있', '거품', '부드럽', '깔끔']
['목', '넘기', '부드럽']
2 2
0.4 0.6666666666666666
4941
['맛', '거품', '맥주', '부드럽', '독특']
['맛', '맛있', '거품', '부드럽', '깔끔']
['거품', '맛']
3 2
0.6 1.0
10127
['맛', '거품', '맥주', '부드럽', '다르']
['맛', '맛있', '거품', '부드럽', '깔끔']
['보리', '쓴맛', '거품', '맥주', '부드럽', '다르']
3 4
0.6 0.6666666666666666
8194
['목', '넘기', '

['어디', '맛', '구하', '편하', '깔끔']
['수', '구하']
['맛', '순', '마시', '편하', '깔끔']
1 3
0.5 0.6
8906
['사람', '시키']
['수', '마시', '구하', '친근']
['사람', '주위', '마시']
0 1
0.0 0.3333333333333333
5912
['모르', '맛', '팬', '친구']
['수', '마시', '구하', '친근']
['친구', '추천', '시', '트러스']
0 1
0.0 0.25
2794
['마시', '사람', '주위', '카스']
['수', '마시', '구하', '친근']
['카스', '맥주', '마시', '주위', '사람']
1 4
0.25 0.6666666666666666
8207
['맛', '대중', '마시', '사람', '거리낌', '깔끔']
['수', '마시', '구하', '친근']
['맛', '대중', '마시', '주위', '사람', '깔끔']
1 5
0.25 0.8333333333333334
7578
['친구', '마시', '친근']
['수', '마시', '구하', '친근']
['친구', '추천']
2 1
0.5 0.5
362
['판매', '친근']
['수', '마시', '구하', '친근']
[]
1 0
0.25 0
6441
['맛', '기호식품', '사람', '즐기', '상쾌', '수']
['수', '마시', '구하', '친근']
['사람', '주위', '마시']
1 1
0.25 0.3333333333333333
3714
['제일', '부산', '마시', '하이트', '사람']
['수', '마시', '구하', '친근']
['사람', '주위', '마시']
1 2
0.25 0.6666666666666666
2054
['폭탄주', '때', '특징', '맛', '마실', '흔하', '마시', '친근']
['수', '마시', '구하', '친근']
['때', '맛', '마실', '넘기', '독하', '친근', '목']
2 4
0.5 0.5714285714285714
668

['깔끔', '깨끗', '뒷맛']
['깔끔', '진하', '맛', '뒷맛']
2 4
0.6666666666666666 1.0
7657
['거', '깔끔', '마시', '뒷맛']
['깔끔', '깨끗', '뒷맛']
['거', '깔끔', '뒷맛']
2 3
0.6666666666666666 1.0
8541
['칼로리', '끝', '맛', '진실', '로우', '깔끔', '모르']
['깔끔', '깨끗', '뒷맛']
['끝', '맛']
1 2
0.3333333333333333 1.0
8368
['쓴맛', '땡기']
['깔끔', '깨끗', '뒷맛']
['쓴맛']
0 1
0.0 1.0
7210
['탄산', '쓴맛', '느끼', '깔끔', '적당']
['깔끔', '깨끗', '뒷맛']
['탄산', '깔끔', '거', '적당']
1 3
0.3333333333333333 0.75
45
['맛', '맛있', '뒷맛', '매력', '개운']
['깔끔', '깨끗', '뒷맛']
['맛있', '거품', '뒷맛', '매력', '개운']
1 4
0.3333333333333333 0.8
6494
['음식', '맛있']
['깔끔', '깨끗', '뒷맛']
['맥주', '수입']
0 0
0.0 0.0
883
['깔끔', '느낌', '뒷맛']
['깔끔', '깨끗', '뒷맛']
[]
2 0
0.6666666666666666 0
5944
['개운', '칼로리', '깔끔', '뒷맛']
['깔끔', '깨끗', '뒷맛']
['깔끔']
2 1
0.6666666666666666 1.0
9356
['덜하', '쓴맛']
['깔끔', '깨끗', '뒷맛']
['쓴맛']
0 1
0.0 1.0
5518
['목', '넘기', '쓴맛', '부드럽']
['깔끔', '깨끗', '뒷맛']
['목', '넘기', '쓴맛', '부드럽']
0 4
0.0 1.0
8878
['깔끔', '개운', '맛', '뒷맛']
['깔끔', '깨끗', '뒷맛']
['깔끔', '개운', '맛', '뒷맛']
2 4
0.6666666666666666 1.0
933

['과일', '거품', '풍부', '부드럽', '향']
['탄산', '보리', '맛', '풍부', '부드럽']
['부드럽', '거품', '풍부', '때문']
2 3
0.4 0.75
2752
['맛', '넘기', '거품', '풍부', '호가든', '부드럽', '목']
['탄산', '보리', '맛', '풍부', '부드럽']
['맛', '넘기', '거품', '때문', '부드럽', '목', '향']
3 5
0.6 0.7142857142857143
804
['때', '쓴맛', '것', '마실', '거품', '맥주', '풍부', '넘기', '부드럽', '목', '비하']
['탄산', '보리', '맛', '풍부', '부드럽']
['때', '쓴맛', '마실', '넘기', '목']
2 5
0.4 1.0
5243
['탄산', '보리', '풍부', '국산', '느낌', '중', '향']
['탄산', '보리', '맛', '풍부', '부드럽']
[]
3 0
0.6 0
5211
['맛', '넘기', '거품', '풍부', '부드럽', '목', '향']
['탄산', '보리', '맛', '풍부', '부드럽']
['목', '넘기', '맥주', '부드럽']
3 3
0.6 0.75
5623
['보리', '넘기', '거품', '풍부', '느끼', '부드럽', '목', '향']
['탄산', '보리', '맛', '풍부', '부드럽']
['맛', '거품', '풍미', '때문', '부드럽', '향']
3 3
0.6 0.42857142857142855
7549
['맛있', '거품', '풍부', '꺼지', '부드럽']
['탄산', '보리', '맛', '풍부', '부드럽']
['향', '맛', '맛있', '부드럽']
2 2
0.4 0.5
2915
['것', '거품', '구하', '부드럽', '이용']
['탄산', '보리', '맛', '풍부', '부드럽']
['맛', '거품', '구하', '부드럽', '때문', '향', '수']
1 3
0.2 0.42857142857142855


In [125]:
#{clusternum(raw기준):[[docno(raw기준), selection]]}
result={}

for clusterno in docno_cluster.keys(): #모든 cluster에 대해서
    
    if clusterno in select_cluster: #Entropy 기준에 해당하는 cluster에 대해서
    
        raw_titleno = num_title_raw_cosine[clusterno]
        raw_title_token = raw_docno_token[raw_titleno] # title token (raw data)
        
        result_docno_titleselect=[]

        for docno in docno_cluster[clusterno]:
            rawdoc_token=raw_docno_token[docno] # rawdoc token (원문 token)
            parse_clusternum=parsingdict[docno] # parsing data cluster number
            all_parse_title_token=[]
            docno_titleselect=[]
            print(docno)
            
            flag = 0
            docno_titleselect.append(docno)
            for parse_clno in parse_clusternum:
                parse_select_result=[]
                parse_titleno=parse_num_title_raw_cosine[parse_clno]
                all_parse_title_token = parse_docno_token[parse_titleno] #각 doc별 다중코딩 총 title token
                parse_select_result.append(parse_clno)
                parse_select_result.append(parse_title_raw_cosine[parse_clno])

                raw_matchcount=0
                parse_matchcount=0
                print(list(set(rawdoc_token)))
                print(list(set(raw_title_token)))
                print(list(set(all_parse_title_token)))

                
                #기본 매칭 개수 --------------method 1-------------
                for i in list(set(rawdoc_token)):
                    raw_matchcount+=list(set(raw_title_token)).count(i)
                    parse_matchcount+=list(set(all_parse_title_token)).count(i)
                print("매칭 개수")
                print(raw_matchcount,parse_matchcount)
                

                #분수형태: -------------method 2-------------
                if len(raw_title_token) != 0:
                    raw_matchscore = raw_matchcount/len(set(raw_title_token))
                else:
                    raw_matchscore=0
                if len(all_parse_title_token) != 0:
                    parse_matchscore = parse_matchcount/len(set(all_parse_title_token))
                else:
                    parse_matchscore=0
#                 print("분수")
#                 print(raw_matchscore,parse_matchscore)
                
                #자카드: -------------method 3-------------  
                if len(raw_title_token) != 0:
                    raw_matchscore_jaccard = raw_matchcount/len(list(set(list(set(raw_title_token))+list(set(rawdoc_token)))))
                else:
                    raw_matchscore_jaccard=0
                if len(all_parse_title_token) != 0:
                    parse_matchscore_jaccard = parse_matchcount/len(list(set(list(set(all_parse_title_token))+list(set(rawdoc_token)))))
                else:
                    parse_matchscore_jaccard=0               
                
                print("jaccard")
                print(list(set(list(set(raw_title_token))+list(set(rawdoc_token)))))
                print(list(set(list(set(all_parse_title_token))+list(set(rawdoc_token)))))
                print(raw_matchscore_jaccard,parse_matchscore_jaccard)
                

        #         if raw_matchcount >= parse_matchcount :  # -------method1
#                 if raw_matchscore >= parse_matchscore :  #----------method2
                if raw_matchscore_jaccard >= parse_matchscore_jaccard :  #--------method3
                    selection=0 #raw title선택
#                     docno_titleselect.append(selection)
#                     docno_titleselect.append(title_raw_cosine[clusterno])
                else : 
                    selection=1 #parsing title선택
                    if flag == 0 :
                        docno_titleselect.append(selection)
                    print(parse_select_result)
                    docno_titleselect.extend(parse_select_result)
                    flag+=1
            
            if flag == 0:
                docno_titleselect.append(0)
                docno_titleselect.append(title_raw_cosine[clusterno])

            print(docno_titleselect)
            result_docno_titleselect.append(docno_titleselect)

        result[clusterno] = result_docno_titleselect
    
    else: # Entropy에서 기준이상 아닌 cluster
        result_docno_titleselect=[]
        for docno in docno_cluster[clusterno]:
            docno_titleselect=[]
            docno_titleselect.append(docno)
            selection=0
            docno_titleselect.append(selection)
            docno_titleselect.append(title_raw_cosine[clusterno])
            result_docno_titleselect.append(docno_titleselect)
        result[clusterno] = result_docno_titleselect
    

9096
['형', '비싸', '맛', '괜찮', '가격', '출시', '병', '상품', '캔', '부수', '집', '디자인', '럼주']
['흔하', '국산', '가격']
['맛', '순함']
매칭 개수
1 1
jaccard
['비싸', '형', '맛', '괜찮', '가격', '출시', '흔하', '병', '상품', '국산', '캔', '부수', '집', '디자인', '럼주']
['비싸', '형', '맛', '괜찮', '가격', '출시', '병', '상품', '캔', '부수', '순함', '집', '디자인', '럼주']
0.06666666666666667 0.07142857142857142
['18', '맛이 순함']
['형', '비싸', '맛', '괜찮', '가격', '출시', '병', '상품', '캔', '부수', '집', '디자인', '럼주']
['흔하', '국산', '가격']
['눈', '상품', '마시', '그렇']
매칭 개수
1 1
jaccard
['비싸', '형', '맛', '괜찮', '가격', '출시', '흔하', '병', '상품', '국산', '캔', '부수', '집', '디자인', '럼주']
['형', '비싸', '맛', '괜찮', '가격', '출시', '눈', '상품', '마시', '병', '캔', '그렇', '부수', '집', '디자인', '럼주']
0.06666666666666667 0.0625
[9096, 1, '18', '맛이 순함']
2530
['비싸', '가격', '병', '맥주', '마시', '맞이', '브랜드', '즐기', '비하']
['흔하', '국산', '가격']
['독하']
매칭 개수
1 0
jaccard
['비싸', '가격', '흔하', '병', '맥주', '마시', '국산', '맞이', '브랜드', '즐기', '비하']
['비싸', '가격', '병', '맥주', '마시', '독하', '맞이', '브랜드', '즐기', '비하']
0.09090909090909091 0.0
['비싸', '가격', '병', '맥주', 

매칭 개수
1 2
jaccard
['탄산', '맛', '세', '부드럽', '깔끔', '강하']
['맛', '강하', '부드럽']
0.16666666666666666 0.6666666666666666
['54', '톡쏘는 맛이 강하고']
['강하', '맛', '부드럽']
['탄산', '깔끔', '맛', '세']
['부드럽']
매칭 개수
1 1
jaccard
['탄산', '맛', '세', '부드럽', '깔끔', '강하']
['맛', '강하', '부드럽']
0.16666666666666666 0.3333333333333333
['22', '부드럽다']
[5642, 1, '54', '톡쏘는 맛이 강하고', '22', '부드럽다']
7189
['탄산', '강하', '맥주', '맛']
['탄산', '깔끔', '맛', '세']
['탄산']
매칭 개수
2 1
jaccard
['탄산', '맛', '세', '맥주', '깔끔', '강하']
['탄산', '맛', '맥주', '강하']
0.3333333333333333 0.25
[7189, 0, '탄산이 세고 맛이 깔끔함']
2860
['목', '넘기', '맛', '탄산']
['탄산', '깔끔', '맛', '세']
['탄산', '부드럽']
매칭 개수
2 1
jaccard
['탄산', '목', '맛', '세', '넘기', '깔끔']
['탄산', '맛', '넘기', '부드럽', '목']
0.3333333333333333 0.2
[2860, 0, '탄산이 세고 맛이 깔끔함']
8670
['탄산', '나', '시원']
['탄산', '깔끔', '맛', '세']
['시원']
매칭 개수
1 1
jaccard
['탄산', '맛', '세', '시원', '깔끔', '나']
['탄산', '나', '시원']
0.16666666666666666 0.3333333333333333
['16', '시원하고']
['탄산', '나', '시원']
['탄산', '깔끔', '맛', '세']
['나', '맛']
매칭 개수
1 1
jaccard
['탄산', '맛', '세'

매칭 개수
3 2
jaccard
['맥주', '맛있', '부드럽']
['맥주', '맛있', '부드럽']
1.0 0.6666666666666666
['맥주', '맛있', '부드럽']
['맥주', '맛있', '부드럽']
['맛있']
매칭 개수
3 1
jaccard
['맥주', '맛있', '부드럽']
['맥주', '맛있', '부드럽']
1.0 0.3333333333333333
[7342, 0, '맥주가 부드럽고 맛있다']
8127
['것', '맛있', '맥주', '디자인', '마음']
['맥주', '맛있', '부드럽']
['발', '마음', '회수']
매칭 개수
2 1
jaccard
['것', '맛있', '맥주', '부드럽', '디자인', '마음']
['것', '맛있', '맥주', '디자인', '회수', '발', '마음']
0.3333333333333333 0.14285714285714285
['것', '맛있', '맥주', '디자인', '마음']
['맥주', '맛있', '부드럽']
['맥주', '맛있', '때문']
매칭 개수
2 2
jaccard
['것', '맛있', '맥주', '부드럽', '디자인', '마음']
['것', '맛있', '맥주', '때문', '디자인', '마음']
0.3333333333333333 0.3333333333333333
[8127, 0, '맥주가 부드럽고 맛있다']
5902
['맛', '맛있', '맥주', '블루베리', '깔끔']
['맥주', '맛있', '부드럽']
['깔끔', '맛', '제일']
매칭 개수
2 2
jaccard
['맛', '맛있', '맥주', '부드럽', '블루베리', '깔끔']
['맛', '제일', '맛있', '맥주', '블루베리', '깔끔']
0.3333333333333333 0.3333333333333333
['맛', '맛있', '맥주', '블루베리', '깔끔']
['맥주', '맛있', '부드럽']
['맛있']
매칭 개수
2 1
jaccard
['맛', '맛있', '맥주', '부드럽', '블루베리', '깔끔']
['맛

['깔끔', '느낌', '시원']
['맛']
매칭 개수
1 1
jaccard
['맛', '맥주', '시원', '느낌', '깔끔']
['맥주', '맛', '시원']
0.2 0.3333333333333333
['8', '맛이 좋고']
[2492, 1, '16', '시원하고', '31', '맥주 맛이 좋다', '8', '맛이 좋고']
5971
['목', '넘기', '시원', '부드럽', '깔끔']
['깔끔', '느낌', '시원']
['깔끔']
매칭 개수
2 1
jaccard
['목', '넘기', '시원', '느낌', '부드럽', '깔끔']
['목', '넘기', '시원', '부드럽', '깔끔']
0.3333333333333333 0.2
['목', '넘기', '시원', '부드럽', '깔끔']
['깔끔', '느낌', '시원']
['목', '넘기', '부드럽']
매칭 개수
2 3
jaccard
['목', '넘기', '시원', '느낌', '부드럽', '깔끔']
['넘기', '시원', '깔끔', '부드럽', '목']
0.3333333333333333 0.6
['6', '목넘김이 부드럽고']
[5971, 1, '6', '목넘김이 부드럽고']
9652
['깔끔', '맥주', '어울리', '시원']
['깔끔', '느낌', '시원']
['깔끔']
매칭 개수
2 1
jaccard
['어울리', '맥주', '시원', '느낌', '깔끔']
['깔끔', '맥주', '어울리', '시원']
0.4 0.25
['깔끔', '맥주', '어울리', '시원']
['깔끔', '느낌', '시원']
['어울리', '색상']
매칭 개수
2 1
jaccard
['어울리', '맥주', '시원', '느낌', '깔끔']
['어울리', '색상', '맥주', '시원', '깔끔']
0.4 0.2
[9652, 0, '시원하고 깔끔한 느낌']
2639
['깔끔', '맥주', '것', '시원']
['깔끔', '느낌', '시원']
['맥주']
매칭 개수
2 1
jaccard
['것', '맥주', '시원', '느낌', '깔끔']


0.2 0.16666666666666666
['좋아하', '접하', '부드럽', '일본']
['맛있', '부드럽']
['부드럽']
매칭 개수
1 1
jaccard
['맛있', '일본', '좋아하', '접하', '부드럽']
['좋아하', '접하', '부드럽', '일본']
0.2 0.25
['4', '부드럽고']
[9074, 1, '4', '부드럽고']
3373
['맛있', '부드럽']
['맛있', '부드럽']
['부드럽']
매칭 개수
2 1
jaccard
['맛있', '부드럽']
['맛있', '부드럽']
1.0 0.5
['맛있', '부드럽']
['맛있', '부드럽']
['맛있']
매칭 개수
2 1
jaccard
['맛있', '부드럽']
['맛있', '부드럽']
1.0 0.5
[3373, 0, '부드럽고 맛있다']
5459
['도수', '맛', '편', '부드럽', '비하']
['맛있', '부드럽']
['부드럽']
매칭 개수
1 1
jaccard
['맛', '맛있', '편', '부드럽', '비하', '도수']
['도수', '맛', '편', '부드럽', '비하']
0.16666666666666666 0.2
['4', '부드럽고']
['도수', '맛', '편', '부드럽', '비하']
['맛있', '부드럽']
['진하', '것', '비하']
매칭 개수
1 1
jaccard
['맛', '맛있', '편', '부드럽', '비하', '도수']
['맛', '것', '편', '비하', '부드럽', '진하', '도수']
0.16666666666666666 0.14285714285714285
[5459, 1, '4', '부드럽고']
4565
['맛', '입맛', '부드럽']
['맛있', '부드럽']
['맛', '부드럽']
매칭 개수
1 2
jaccard
['입맛', '맛', '맛있', '부드럽']
['맛', '입맛', '부드럽']
0.25 0.6666666666666666
['24', '맛이 부드럽다']
['맛', '입맛', '부드럽']
['맛있', '부드럽']
['입맛']
매칭 

['느낌', '쓴맛']
0.3333333333333333 0.5
['89', '쓴맛이 적다']
[3867, 1, '89', '쓴맛이 적다']
5200
['느낌', '친근']
['이국', '느낌']
['친근']
매칭 개수
1 1
jaccard
['이국', '느낌', '친근']
['느낌', '친근']
0.3333333333333333 0.5
['62_1', '친근하다']
[5200, 1, '62_1', '친근하다']
9534
[9534, 0, '이국적인 느낌이 들어서']
9784
[9784, 0, '이국적인 느낌이 들어서']
1580
['이국', '느낌']
['이국', '느낌']
['느낌']
매칭 개수
2 1
jaccard
['이국', '느낌']
['이국', '느낌']
1.0 0.5
[1580, 0, '이국적인 느낌이 들어서']
7127
['거', '눈', '느낌', '맛있']
['이국', '느낌']
['깔끔', '느낌']
매칭 개수
1 1
jaccard
['맛있', '눈', '거', '이국', '느낌']
['맛있', '눈', '거', '느낌', '깔끔']
0.2 0.2
[7127, 0, '이국적인 느낌이 들어서']
4495
['씁쓸', '느낌', '맛']
['이국', '느낌']
['맛', '일품']
매칭 개수
1 1
jaccard
['이국', '씁쓸', '느낌', '맛']
['씁쓸', '느낌', '맛', '일품']
0.25 0.25
[4495, 0, '이국적인 느낌이 들어서']
8019
['깔끔', '느낌', '맛']
['이국', '느낌']
['느낌']
매칭 개수
1 1
jaccard
['깔끔', '이국', '느낌', '맛']
['깔끔', '느낌', '맛']
0.25 0.3333333333333333
['0', '느낌이 좋다']
['깔끔', '느낌', '맛']
['이국', '느낌']
['깔끔', '맛']
매칭 개수
1 2
jaccard
['깔끔', '이국', '느낌', '맛']
['깔끔', '느낌', '맛']
0.25 0.6666666666666666
['2',

['순', '편하', '마시']
매칭 개수
1 2
jaccard
['마시', '편하', '브랜드', '부드럽', '술', '식']
['마시', '편하', '부드럽', '술', '순']
0.16666666666666666 0.4
['98', '순해서 마시기 편하다']
[8480, 1, '98', '순해서 마시기 편하다']
3506
['정형', '마시', '맥주', '사람', '브랜드', '나']
['마시', '브랜드', '식']
['게', '것', '시원']
매칭 개수
2 0
jaccard
['정형', '마시', '맥주', '사람', '브랜드', '나', '식']
['것', '정형', '마시', '맥주', '시원', '사람', '브랜드', '게', '나']
0.2857142857142857 0.0
[3506, 0, '가끔식 마시는 브랜드라서']
2466
['때', '깨끗', '넘기', '마시', '맥주', '느낌', '부', '목']
['마시', '브랜드', '식']
['때', '맥주', '반하', '일본']
매칭 개수
1 2
jaccard
['때', '깨끗', '넘기', '마시', '맥주', '느낌', '브랜드', '부', '목', '식']
['때', '반하', '일본', '깨끗', '넘기', '맥주', '마시', '느낌', '부', '목']
0.1 0.2
['103', '일본 갔을 때 생맥주에 반했다']
[2466, 1, '103', '일본 갔을 때 생맥주에 반했다']
8889
['힘들', '마시', '단점', '맥주']
['마시', '브랜드', '식']
['상표', '마시', '맥주']
매칭 개수
1 2
jaccard
['마시', '맥주', '힘들', '단점', '브랜드', '식']
['마시', '맥주', '힘들', '단점', '상표']
0.16666666666666666 0.4
['76', '자주 마시는 맥주상표고']
['힘들', '마시', '단점', '맥주']
['마시', '브랜드', '식']
['마시']
매칭 개수
1 1
jaccard
['마시', '

['탄산', '덜하', '쓴맛', '맛', '술', '깔끔', '적당']
['탄산', '쓴맛', '맛', '술', '깔끔', '적당']
0.2857142857142857 0.16666666666666666
['쓴맛', '맛', '술', '깔끔', '적당']
['탄산', '덜하', '쓴맛', '적당']
['부드럽', '맥스', '경우', '술']
매칭 개수
2 1
jaccard
['탄산', '덜하', '쓴맛', '맛', '술', '깔끔', '적당']
['쓴맛', '맛', '맥스', '부드럽', '술', '깔끔', '경우', '적당']
0.2857142857142857 0.125
['쓴맛', '맛', '술', '깔끔', '적당']
['탄산', '덜하', '쓴맛', '적당']
['깔끔']
매칭 개수
2 1
jaccard
['탄산', '덜하', '쓴맛', '맛', '술', '깔끔', '적당']
['쓴맛', '맛', '술', '깔끔', '적당']
0.2857142857142857 0.2
[1481, 0, '쓴맛이 덜하고 적당한 탄산']
1181
['알콜']
['탄산', '덜하', '쓴맛', '적당']
['탄산', '거', '적당']
매칭 개수
0 0
jaccard
['탄산', '덜하', '쓴맛', '알콜', '적당']
['탄산', '알콜', '거', '적당']
0.0 0.0
[1181, 0, '쓴맛이 덜하고 적당한 탄산']
3345
['맥주', '알콜', '도수']
['탄산', '덜하', '쓴맛', '적당']
['맥주']
매칭 개수
0 1
jaccard
['탄산', '덜하', '쓴맛', '도수', '맥주', '알콜', '적당']
['맥주', '알콜', '도수']
0.0 0.3333333333333333
['32', '다른 맥주보다']
['맥주', '알콜', '도수']
['탄산', '덜하', '쓴맛', '적당']
['수', '구하']
매칭 개수
0 0
jaccard
['탄산', '덜하', '쓴맛', '도수', '맥주', '알콜', '적당']
['맥주', '구하', '알콜

0.4 0.25
[1651, 0, '맛이 괜찮고 디자인이 깔끔하다']
6773
['맛', '후원', '공식', '이미지', '챔스', '디자인', '마음']
['깔끔', '디자인', '맛', '괜찮']
['맛', '순함']
매칭 개수
2 1
jaccard
['맛', '괜찮', '후원', '공식', '이미지', '챔스', '깔끔', '디자인', '마음']
['맛', '후원', '공식', '이미지', '순함', '챔스', '디자인', '마음']
0.2222222222222222 0.125
['맛', '후원', '공식', '이미지', '챔스', '디자인', '마음']
['깔끔', '디자인', '맛', '괜찮']
['발', '마음', '회수']
매칭 개수
2 1
jaccard
['맛', '괜찮', '후원', '공식', '이미지', '챔스', '깔끔', '디자인', '마음']
['맛', '후원', '디자인', '공식', '회수', '이미지', '챔스', '발', '마음']
0.2222222222222222 0.1111111111111111
[6773, 0, '맛이 괜찮고 디자인이 깔끔하다']
7893
['깔끔', '병', '디자인']
['깔끔', '디자인', '맛', '괜찮']
['병', '예쁘']
매칭 개수
2 1
jaccard
['맛', '괜찮', '병', '깔끔', '디자인']
['깔끔', '병', '디자인', '예쁘']
0.4 0.25
[7893, 0, '맛이 괜찮고 디자인이 깔끔하다']
1326
['넘기', '이미지', '브랜드', '부드럽', '목', '디자인']
['깔끔', '디자인', '맛', '괜찮']
['목', '넘기', '부드럽']
매칭 개수
1 3
jaccard
['목', '맛', '괜찮', '넘기', '이미지', '브랜드', '부드럽', '깔끔', '디자인']
['넘기', '이미지', '브랜드', '부드럽', '목', '디자인']
0.1111111111111111 0.5
['6', '목넘김이 부드럽고']
['넘기', '이미지', '브랜드', '부

In [104]:
result

{'0': [[8828, 0, '시원하다'],
  [2951, 0, '시원하다'],
  [8632, 0, '시원하다'],
  [8448, 0, '시원하다'],
  [10013, 0, '시원하다'],
  [5086, 0, '시원하다'],
  [9394, 0, '시원하다'],
  [8762, 0, '시원하다'],
  [5763, 0, '시원하다'],
  [7968, 0, '시원하다'],
  [908, 0, '시원하다'],
  [297, 0, '시원하다'],
  [1554, 0, '시원하다'],
  [5961, 0, '시원하다'],
  [3432, 0, '시원하다'],
  [7292, 0, '시원하다'],
  [2549, 0, '시원하다'],
  [7396, 0, '시원하다'],
  [1014, 0, '시원하다'],
  [5772, 0, '시원하다'],
  [8129, 0, '시원하다'],
  [4148, 0, '시원하다'],
  [7057, 0, '시원하다'],
  [4203, 0, '시원하다'],
  [3651, 0, '시원하다'],
  [6459, 0, '시원하다'],
  [6809, 0, '시원하다'],
  [2446, 0, '시원하다'],
  [9155, 0, '시원하다'],
  [4528, 0, '시원하다'],
  [6088, 0, '시원하다'],
  [6316, 0, '시원하다'],
  [4564, 0, '시원하다'],
  [3333, 0, '시원하다'],
  [10344, 0, '시원하다'],
  [8856, 0, '시원하다'],
  [9480, 0, '시원하다'],
  [6619, 0, '시원하다'],
  [4042, 0, '시원하다'],
  [8584, 0, '시원하다'],
  [9567, 0, '시원하다'],
  [3351, 0, '시원하다'],
  [6368, 0, '시원하다'],
  [8203, 0, '시원하다'],
  [9274, 0, '시원하다'],
  [2526, 0, '시원하다'],
  [2724, 0, '시원하다'],
  [4745,

In [122]:
rows=[]
for key in result.keys():
    for i in result[key]:
        row=[]
        row.append(key)
        row.extend(i)
        row.insert(2, raw_docs[row[1]])
        rows.append(row)

In [101]:
rows

[['0', 8828, '시원하다', 0, '시원하다'],
 ['0', 2951, '시원한맛', 0, '시원하다'],
 ['0', 8632, '시원', 0, '시원하다'],
 ['0', 8448, 'ㅈ다른 것 보다 더 시원한 맛이 난다', 0, '시원하다'],
 ['0', 10013, '병을 딸때 시원하게 펑하는 소리가 나고, 맛도 좋은 것 같다', 0, '시원하다'],
 ['0', 5086, '시원하고 탁 쏘는 맛이 봏아서', 0, '시원하다'],
 ['0', 9394, '시원함', 0, '시원하다'],
 ['0', 8762, '시원해서', 0, '시원하다'],
 ['0', 5763, '시원한 맛', 0, '시원하다'],
 ['0', 7968, '맛이시원하다', 0, '시원하다'],
 ['0', 908, '시원함', 0, '시원하다'],
 ['0', 297, '시원한 맛', 0, '시원하다'],
 ['0', 1554, '톡 쏘고 시원하다', 0, '시원하다'],
 ['0', 5961, '쌉살함 깔금함 시원함', 0, '시원하다'],
 ['0', 3432, '시원해서', 0, '시원하다'],
 ['0', 7292, '시원하다', 0, '시원하다'],
 ['0', 2549, '시원합', 0, '시원하다'],
 ['0', 7396, '톡쏘는 맛이 시원함.', 0, '시원하다'],
 ['0', 1014, '톡쏘는 맛이 있다 그리고 시원하다', 0, '시원하다'],
 ['0', 5772, '시원하고 맛이좋다', 0, '시원하다'],
 ['0', 8129, '시원한맛', 0, '시원하다'],
 ['0', 4148, '시원한맛', 0, '시원하다'],
 ['0', 7057, '시원해서', 0, '시원하다'],
 ['0', 4203, '시원해요~', 0, '시원하다'],
 ['0', 3651, '시원한 맛과 쌉싸름한 맛이 좋음', 0, '시원하다'],
 ['0', 6459, '시원하다', 0, '시원하다'],
 ['0', 6809, '시원함', 0, '시원하다'],
 ['

In [123]:
with open('selection_output1218_method3.csv', 'w', newline='', encoding='CP949') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['clusterNo','docno','doc','selection'])
    writer.writerows(rows)

### test